<a href="https://colab.research.google.com/github/Noonanav/phage_host_set_transformers/blob/main/mean_pooling_optuna_glm_cv.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

"""
# Pooling-Based Architecture with Optuna Hyperparameter Optimization

This notebook implements hyperparameter optimization for a simple pooling-based architecture
for strain-phage interaction prediction using Optuna. It's adapted from the set transformer
optimization workflow but uses a simpler architecture based on mean/max/median pooling.
"""

In [ ]:
!pip install optuna pandas numpy torch matplotlib seaborn scikit-learn
!pip install plotly kaleido
!pip install optuna-integration[pytorch_lightning]

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 386.6/386.6 kB 23.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 3.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 101.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 83.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 50.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 41.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 19.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 4.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 108.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 231.9/231.9 kB 22.4 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitli

In [ ]:
# Setup and imports
import os
import pickle
import datetime
import numpy as np
import pandas as pd
import torch
import torch.nn as nn
import torch.nn.functional as F
import optuna
from optuna.pruners import MedianPruner
from optuna.samplers import TPESampler
import matplotlib.pyplot as plt
import seaborn as sns
from pathlib import Path
from typing import Dict, List, Tuple, Optional
from sklearn.model_selection import train_test_split
from sklearn.metrics import (
    accuracy_score, precision_score, recall_score, f1_score,
    matthews_corrcoef, roc_auc_score, average_precision_score, confusion_matrix,
    roc_curve, precision_recall_curve, auc
)
from tqdm import tqdm
import json

# Set up result directory with timestamp
timestamp = datetime.datetime.now().strftime("%Y%m%d_%H%M%S")
RESULTS_DIR = f"optuna_pooling_results_{timestamp}"
os.makedirs(RESULTS_DIR, exist_ok=True)
os.makedirs(os.path.join(RESULTS_DIR, "plots"), exist_ok=True)
os.makedirs(os.path.join(RESULTS_DIR, "models"), exist_ok=True)
os.makedirs(os.path.join(RESULTS_DIR, "metrics"), exist_ok=True)

# Set device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(f"Using device: {device}")

# Mount Google Drive if in Colab
try:
    from google.colab import drive
    drive.mount('/content/drive')
    IN_COLAB = True
except:
    IN_COLAB = False
    print("Not running in Colab, skipping drive mount")

Using device: cuda
Mounted at /content/drive


## Data Loading and Processing Functions

In [ ]:
def load_embeddings_flexible(embedding_dir, genome_ids_csv=None, id_column="genome_id"):
    """Load embeddings from a directory with support for multiple formats."""
    embedding_dir = Path(embedding_dir)
    embeddings = {}

    # If genome_ids_csv is provided, load specific genome IDs
    genome_ids = None
    if genome_ids_csv:
        try:
            genome_df = pd.read_csv(genome_ids_csv)
            if id_column not in genome_df.columns:
                raise ValueError(f"Column '{id_column}' not found in {genome_ids_csv}")
            genome_ids = set(genome_df[id_column].astype(str))
            print(f"Loaded {len(genome_ids)} genome IDs from {genome_ids_csv}")
        except Exception as e:
            print(f"Error loading genome IDs: {e}")
            print("Falling back to loading all embeddings")
            genome_ids = None

    # Get list of all embedding files
    file_paths = list(embedding_dir.glob('*.npy'))
    if not file_paths:
        print(f"No .npy files found in {embedding_dir}")
        return embeddings

    # Track which genomes were found
    found_genomes = set()

    # Process each file
    for file_path in file_paths:
        identifier = file_path.stem  # filename without extension

        # Skip if not in the list of genome IDs (if a list was provided)
        if genome_ids is not None and identifier not in genome_ids:
            continue

        try:
            embedding_data = np.load(file_path, allow_pickle=True)

            # Detect and process based on file format
            if isinstance(embedding_data, np.ndarray):
                # If it's a simple array with shape [num_genes, embedding_dim]
                if embedding_data.ndim == 2:
                    # Create generic gene IDs
                    gene_ids = [f"{identifier}_gene_{i+1}" for i in range(embedding_data.shape[0])]
                    embeddings[identifier] = (embedding_data, gene_ids)
                    format_type = "simple_array"

                # If it's a dictionary-like object in a 0-d array
                elif hasattr(embedding_data.item(), 'keys'):
                    embeddings_dict = embedding_data.item()
                    gene_ids = list(embeddings_dict.keys())
                    embedding_list = [embeddings_dict[gene_id] for gene_id in gene_ids]

                    if not embedding_list:
                        print(f"Warning: No embeddings found in {file_path}")
                        continue

                    embeddings_array = np.stack(embedding_list)
                    embeddings[identifier] = (embeddings_array, gene_ids)
                    format_type = "dict_format"
                else:
                    print(f"Warning: Unrecognized array format for {file_path}")
                    continue
            else:
                print(f"Warning: Unrecognized data type for {file_path}")
                continue

            found_genomes.add(identifier)

        except Exception as e:
            print(f"Error loading {file_path}: {e}")

    # Report on results
    print(f"Successfully loaded {len(embeddings)} embeddings")

    # If genome IDs were provided, report on missing genomes
    if genome_ids is not None:
        missing_genomes = genome_ids - found_genomes
        if missing_genomes:
            print(f"Warning: {len(missing_genomes)} genomes from the CSV were not found")

    return embeddings

def filter_interactions_by_strain(interactions_df, random_state=42):
    """Split interactions into train/test by strain."""
    unique_strains = interactions_df['strain'].unique()
    train_strains, test_strains = train_test_split(
        unique_strains,
        test_size=0.2,
        random_state=random_state
    )

    train_df = interactions_df[interactions_df['strain'].isin(train_strains)]
    test_df = interactions_df[interactions_df['strain'].isin(test_strains)]

    print(f"Train set: {len(train_df)} interactions, {len(train_strains)} strains")
    print(f"Test set:  {len(test_df)} interactions, {len(test_strains)} strains")
    return train_df, test_df

def calculate_phage_specific_weights(train_df):
    """Calculate positive weights for each phage based on its interaction distribution."""
    phage_weights = {}

    for phage in train_df['phage'].unique():
        phage_df = train_df[train_df['phage'] == phage]
        num_pos = (phage_df['interaction'] == 1).sum()
        num_neg = (phage_df['interaction'] == 0).sum()

        if num_pos > 0:
            # Calculate the weight as negative/positive ratio
            weight = num_neg / num_pos
            # Clip extremely high values
            weight = min(max(weight, 1.0), 10.0)
        else:
            # If no positive examples, use a default high weight
            weight = 5.0

        phage_weights[phage] = weight

    return phage_weights

class PrecomputedPooledDataset(torch.utils.data.Dataset):
    def __init__(self, interactions_df, pooled_strains, pooled_phages, phage_weights):
        """Dataset for interactions with precomputed pooled embeddings."""
        self.interactions = interactions_df.reset_index(drop=True)
        self.pooled_strains = pooled_strains
        self.pooled_phages = pooled_phages
        self.phage_weights = phage_weights

        # Check for missing embeddings
        missing_strains = set(self.interactions['strain']) - set(pooled_strains.keys())
        missing_phages = set(self.interactions['phage']) - set(pooled_phages.keys())

        if missing_strains or missing_phages:
            raise ValueError(
                f"Missing embeddings for {len(missing_strains)} strains "
                f"and {len(missing_phages)} phages."
            )

    def __len__(self):
        return len(self.interactions)

    def __getitem__(self, idx):
        row = self.interactions.iloc[idx]
        strain_vec = torch.tensor(self.pooled_strains[row['strain']], dtype=torch.float32)
        phage_vec = torch.tensor(self.pooled_phages[row['phage']], dtype=torch.float32)
        label = torch.tensor(row['interaction'], dtype=torch.float32)
        weight = torch.tensor(self.phage_weights.get(row['phage'], 1.0), dtype=torch.float32)

        return strain_vec, phage_vec, label, weight, row['strain'], row['phage']

def create_data_loaders(train_df, test_df, strain_embeddings, phage_embeddings,
                       batch_size=16, use_phage_weights=True):
    """Create data loaders with pooled vectors."""
    # Calculate phage-specific weights
    phage_weights = {}
    if train_df is not None and not train_df.empty:
        if use_phage_weights:
            phage_weights = calculate_phage_specific_weights(train_df)
            print(f"Calculated weights for {len(phage_weights)} phages")
        else:
            # Use a default weight of 1.0 for all phages
            for phage in train_df['phage'].unique():
                phage_weights[phage] = 1.0
            print("Using default weight of 1.0 for all phages")

    # Precompute pooled embeddings using best pooling type
    pooled_strains, pooled_phages = precompute_pooled_embeddings(
        strain_embeddings, phage_embeddings,
        pooling_type=best_params['pooling_type'] if 'best_params' in globals() else 'mean'
    )

    # Create datasets
    train_dataset = PrecomputedPooledDataset(train_df, pooled_strains, pooled_phages, phage_weights)
    test_dataset = PrecomputedPooledDataset(test_df, pooled_strains, pooled_phages, phage_weights)

    # Create data loaders
    train_loader = torch.utils.data.DataLoader(
        train_dataset,
        batch_size=batch_size,
        shuffle=True,
        collate_fn=collate_pooled_vectors
    )

    test_loader = torch.utils.data.DataLoader(
        test_dataset,
        batch_size=batch_size,
        shuffle=False,
        collate_fn=collate_pooled_vectors
    )

    return train_loader, test_loader

## Enhanced Pooling Model

In [ ]:
def precompute_pooled_embeddings(strain_embeddings, phage_embeddings, pooling_type='mean'):
    """Precompute pooled embeddings for all strains and phages."""
    pooled_strains = {}
    pooled_phages = {}

    # Apply pooling to each strain
    print(f"Precomputing {pooling_type} pooling for {len(strain_embeddings)} strains...")
    for strain_id, (embedding, _) in strain_embeddings.items():
        # Convert to tensor
        embedding_tensor = torch.tensor(embedding, dtype=torch.float32)

        # Apply pooling
        if pooling_type == 'mean':
            pooled = torch.mean(embedding_tensor, dim=0)
        elif pooling_type == 'max':
            pooled = torch.max(embedding_tensor, dim=0)[0]
        elif pooling_type == 'median':
            pooled = torch.median(embedding_tensor, dim=0)[0]
        else:
            raise ValueError(f"Unknown pooling type: {pooling_type}")

        # Store pooled vector
        pooled_strains[strain_id] = pooled.numpy()

    # Apply pooling to each phage
    print(f"Precomputing {pooling_type} pooling for {len(phage_embeddings)} phages...")
    for phage_id, (embedding, _) in phage_embeddings.items():
        # Convert to tensor
        embedding_tensor = torch.tensor(embedding, dtype=torch.float32)

        # Apply pooling
        if pooling_type == 'mean':
            pooled = torch.mean(embedding_tensor, dim=0)
        elif pooling_type == 'max':
            pooled = torch.max(embedding_tensor, dim=0)[0]
        elif pooling_type == 'median':
            pooled = torch.median(embedding_tensor, dim=0)[0]
        else:
            raise ValueError(f"Unknown pooling type: {pooling_type}")

        # Store pooled vector
        pooled_phages[phage_id] = pooled.numpy()

    return pooled_strains, pooled_phages

class PrecomputedPooledDataset(torch.utils.data.Dataset):
    def __init__(self, interactions_df, pooled_strains, pooled_phages, phage_weights):
        """Dataset for interactions with precomputed pooled embeddings."""
        self.interactions = interactions_df.reset_index(drop=True)
        self.pooled_strains = pooled_strains
        self.pooled_phages = pooled_phages
        self.phage_weights = phage_weights

        # Check for missing embeddings
        missing_strains = set(self.interactions['strain']) - set(pooled_strains.keys())
        missing_phages = set(self.interactions['phage']) - set(pooled_phages.keys())

        if missing_strains or missing_phages:
            raise ValueError(
                f"Missing embeddings for {len(missing_strains)} strains "
                f"and {len(missing_phages)} phages."
            )

    def __len__(self):
        return len(self.interactions)

    def __getitem__(self, idx):
        row = self.interactions.iloc[idx]
        strain_vec = torch.tensor(self.pooled_strains[row['strain']], dtype=torch.float32)
        phage_vec = torch.tensor(self.pooled_phages[row['phage']], dtype=torch.float32)
        label = torch.tensor(row['interaction'], dtype=torch.float32)
        weight = torch.tensor(self.phage_weights.get(row['phage'], 1.0), dtype=torch.float32)

        return strain_vec, phage_vec, label, weight, row['strain'], row['phage']

class PooledVectorModel(nn.Module):
    """A simplified model that takes pre-pooled vectors as input."""
    def __init__(self, embedding_dim=384,
                 dropout=0.1,
                 ln=True,
                 classifier_hidden_layers=1,
                 classifier_hidden_dim=None,
                 activation_function="relu"):
        super().__init__()

        # Set hidden dim for classifier if not provided
        if classifier_hidden_dim is None:
            classifier_hidden_dim = embedding_dim

        # Determine activation function
        if activation_function == "relu":
            self.activation = nn.ReLU()
        elif activation_function == "gelu":
            self.activation = nn.GELU()
        elif activation_function == "silu":
            self.activation = nn.SiLU()
        else:
            self.activation = nn.ReLU()

        # Build classifier with dynamic number of layers
        classifier_layers = []

        # Input layer
        classifier_layers.append(nn.Linear(embedding_dim * 2, classifier_hidden_dim))
        classifier_layers.append(nn.LayerNorm(classifier_hidden_dim) if ln else nn.Identity())
        classifier_layers.append(self.activation)
        classifier_layers.append(nn.Dropout(dropout))

        # Hidden layers
        for _ in range(classifier_hidden_layers - 1):
            classifier_layers.append(nn.Linear(classifier_hidden_dim, classifier_hidden_dim))
            classifier_layers.append(nn.LayerNorm(classifier_hidden_dim) if ln else nn.Identity())
            classifier_layers.append(self.activation)
            classifier_layers.append(nn.Dropout(dropout))

        # Output layer
        classifier_layers.append(nn.Linear(classifier_hidden_dim, 1))

        self.classifier = nn.Sequential(*classifier_layers)

    def forward(self, strain_vec, phage_vec):
        """Forward pass for pre-pooled vectors."""
        # Concatenate strain and phage representations
        combined = torch.cat([strain_vec, phage_vec], dim=-1)  # [B, 2*D]

        # Apply the classifier
        logits = self.classifier(combined)  # [B, 1]

        return logits

def collate_pooled_vectors(batch):
    """Collate function for pre-computed pooled vectors."""
    # Unpack the batch
    strains, phages, labels, weights, strain_ids, phage_ids = zip(*batch)

    # Stack vectors
    strain_batch = torch.stack(strains)  # [B, D]
    phage_batch = torch.stack(phages)    # [B, D]

    # Prepare labels and weights
    label_batch = torch.tensor(labels, dtype=torch.float32).unsqueeze(1)  # [B, 1]
    weight_batch = torch.tensor(weights, dtype=torch.float32).unsqueeze(1)  # [B, 1]

    return strain_batch, phage_batch, label_batch, weight_batch, strain_ids, phage_ids

## Training and Evaluation Functions


## Visualization Functions

In [ ]:
class EarlyStopping:
    """Early stopping to stop training when a metric has stopped improving."""
    def __init__(self, patience=7, min_delta=0.0, mode='max'):
        self.patience = patience
        self.min_delta = min_delta
        self.mode = mode  # 'max' or 'min'
        self.best_metric = None
        self.counter = 0
        self.early_stop = False

    def __call__(self, current_metric):
        if self.best_metric is None:
            self.best_metric = current_metric
        else:
            # For 'max' mode, improvement means current_metric >= best_metric + min_delta
            if self.mode == 'max':
                if current_metric < (self.best_metric + self.min_delta):
                    self.counter += 1
                else:
                    self.best_metric = current_metric
                    self.counter = 0
            else:  # 'min' mode
                if current_metric > (self.best_metric - self.min_delta):
                    self.counter += 1
                else:
                    self.best_metric = current_metric
                    self.counter = 0

            if self.counter >= self.patience:
                self.early_stop = True

        return self.best_metric

def get_scheduler(scheduler_type, optimizer, num_train_steps, warmup_ratio=0.1):
    """Create a learning rate scheduler."""
    if scheduler_type == "one_cycle":
        return torch.optim.lr_scheduler.OneCycleLR(
            optimizer,
            max_lr=optimizer.param_groups[0]['lr'],
            total_steps=num_train_steps,
            pct_start=warmup_ratio
        )
    elif scheduler_type == "cosine_annealing":
        return torch.optim.lr_scheduler.CosineAnnealingLR(
            optimizer,
            T_max=num_train_steps
        )
    elif scheduler_type == "reduce_on_plateau":
        return torch.optim.lr_scheduler.ReduceLROnPlateau(
            optimizer,
            mode='max',
            patience=3,
            factor=0.5
        )
    elif scheduler_type == "linear_warmup_decay":
        # Create a simple linear warmup followed by linear decay
        def lr_lambda(current_step):
            warmup_steps = int(num_train_steps * warmup_ratio)
            if current_step < warmup_steps:
                return float(current_step) / float(max(1, warmup_steps))
            return max(
                0.0,
                float(num_train_steps - current_step) / float(max(1, num_train_steps - warmup_steps))
            )
        return torch.optim.lr_scheduler.LambdaLR(optimizer, lr_lambda)
    else:  # "none" or any other value
        return None

def train_epoch(model, train_loader, optimizer, device, scheduler=None, use_phage_weights=True):
    """Train for one epoch with pooled vectors."""
    model.train()
    total_loss = 0
    all_preds = []
    all_labels = []

    for batch in train_loader:
        # Unpack with weights (first 4 elements for pooled vectors)
        strain_vec, phage_vec, labels, weights = batch[:4]

        strain_vec = strain_vec.to(device)
        phage_vec = phage_vec.to(device)
        labels = labels.to(device)
        weights = weights.to(device) if use_phage_weights else None

        optimizer.zero_grad()
        logits = model(strain_vec, phage_vec)

        # Use batch-specific weights in the loss calculation if enabled
        if use_phage_weights:
            criterion = nn.BCEWithLogitsLoss(pos_weight=weights)
        else:
            criterion = nn.BCEWithLogitsLoss()

        loss = criterion(logits, labels)

        loss.backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)
        optimizer.step()
        if scheduler is not None:
            if not isinstance(scheduler, torch.optim.lr_scheduler.ReduceLROnPlateau):
                scheduler.step()

        total_loss += loss.item()
        preds = torch.sigmoid(logits).reshape(-1).detach().cpu().numpy()
        all_preds.extend(preds)
        all_labels.extend(labels.cpu().numpy())

    epoch_loss = total_loss / len(train_loader)
    binary_preds = (np.array(all_preds) > 0.5).astype(int)
    binary_labels = (np.array(all_labels) > 0.5).astype(int)
    epoch_mcc = matthews_corrcoef(binary_labels, binary_preds)

    return epoch_loss, epoch_mcc

def validate(model, val_loader, device, use_phage_weights=True):
    """Validate the model with pooled vectors."""
    model.eval()
    total_loss = 0
    all_preds = []
    all_labels = []

    with torch.no_grad():
        for batch in val_loader:
            # Unpack with weights (first 4 elements for pooled vectors)
            strain_vec, phage_vec, labels, weights = batch[:4]

            strain_vec = strain_vec.to(device)
            phage_vec = phage_vec.to(device)
            labels = labels.to(device)
            weights = weights.to(device) if use_phage_weights else None

            logits = model(strain_vec, phage_vec)

            # Use batch-specific weights in the loss calculation if enabled
            if use_phage_weights:
                criterion = nn.BCEWithLogitsLoss(pos_weight=weights)
            else:
                criterion = nn.BCEWithLogitsLoss()

            loss = criterion(logits, labels)

            total_loss += loss.item()
            preds = torch.sigmoid(logits).cpu().numpy()
            all_preds.extend(preds)
            all_labels.extend(labels.cpu().numpy())

    val_loss = total_loss / len(val_loader)
    binary_preds = (np.array(all_preds) > 0.5).astype(int)
    binary_labels = (np.array(all_labels) > 0.5).astype(int)
    val_mcc = matthews_corrcoef(binary_labels, binary_preds)

    return val_loss, val_mcc, binary_preds, binary_labels

def evaluate_full(model, data_loader, device, use_phage_weights=True):
    """Comprehensive evaluation with pooled vectors."""
    model.eval()
    all_preds = []
    all_labels = []
    total_loss = 0

    with torch.no_grad():
        for batch in data_loader:
            # Unpack with weights (first 4 elements for pooled vectors)
            strain_vec, phage_vec, labels, weights = batch[:4]

            strain_vec = strain_vec.to(device)
            phage_vec = phage_vec.to(device)
            labels = labels.to(device)
            weights = weights.to(device) if use_phage_weights else None

            logits = model(strain_vec, phage_vec)

            # Calculate loss
            if use_phage_weights:
                criterion = nn.BCEWithLogitsLoss(pos_weight=weights)
            else:
                criterion = nn.BCEWithLogitsLoss()

            loss = criterion(logits, labels)
            total_loss += loss.item()

            preds = torch.sigmoid(logits).cpu().numpy().flatten()
            all_preds.extend(preds)
            all_labels.extend(labels.cpu().numpy().flatten())

    all_preds = np.array(all_preds)
    all_labels = np.array(all_labels)
    loss = total_loss / len(data_loader)

    # Calculate metrics
    binary_preds = (all_preds > 0.5).astype(int)
    accuracy = accuracy_score(all_labels, binary_preds)
    precision = precision_score(all_labels, binary_preds)
    recall = recall_score(all_labels, binary_preds)
    f1 = f1_score(all_labels, binary_preds)
    mcc = matthews_corrcoef(all_labels, binary_preds)
    try:
        roc_auc = roc_auc_score(all_labels, all_preds)
    except:
        roc_auc = 0.5  # Default value when one class only
    try:
        pr_auc = average_precision_score(all_labels, all_preds)
    except:
        pr_auc = 0.5
    conf_matrix = confusion_matrix(all_labels, binary_preds)

    return {
        'loss': total_loss / len(data_loader),
        'accuracy': accuracy_score(all_labels, binary_preds),
        'precision': precision_score(all_labels, binary_preds),
        'recall': recall_score(all_labels, binary_preds),
        'f1': f1_score(all_labels, binary_preds),
        'mcc': matthews_corrcoef(all_labels, binary_preds),
        'roc_auc': roc_auc_score(all_labels, all_preds),
        'pr_auc': average_precision_score(all_labels, all_preds),
        'conf_matrix': confusion_matrix(all_labels, binary_preds),
        'all_preds': all_preds,
        'all_labels': all_labels,
        'binary_preds': binary_preds
    }

def train_model(model, train_loader, val_loader, trial,
                num_epochs=100,
                learning_rate=5e-5,
                patience=7,
                device='cuda',
                use_phage_weights=True,
                scheduler_type="one_cycle",
                warmup_ratio=0.1,
                weight_decay=0.01,
                metrics_dir=None,
                report_to_optuna=True):  # Add this parameter
    """Train model with configurable parameters and Optuna pruning."""
    optimizer = torch.optim.AdamW(
        model.parameters(),
        lr=learning_rate,
        weight_decay=weight_decay
    )

    # Setup scheduler based on type
    num_train_steps = len(train_loader) * num_epochs
    scheduler = get_scheduler(
        scheduler_type,
        optimizer,
        num_train_steps,
        warmup_ratio
    )

    early_stopping = EarlyStopping(patience=patience, mode='max')
    history = {
        'train_loss': [],
        'val_loss': [],
        'train_mcc': [],
        'val_mcc': [],
        'lr': []
    }

    # Initialize metrics DataFrame
    metrics_df = pd.DataFrame(columns=[
        'epoch', 'train_loss', 'val_loss', 'train_mcc', 'val_mcc', 'lr'
    ])
    metrics_records = []  # We'll collect records and create DataFrame at the end

    try:
        for epoch in range(num_epochs):
            # Train and validate
            train_loss, train_mcc = train_epoch(
                model, train_loader, optimizer, device,
                scheduler, use_phage_weights
            )
            val_loss, val_mcc, _, _ = validate(
                model, val_loader, device, use_phage_weights
            )

            # Update history
            history['train_loss'].append(train_loss)
            history['val_loss'].append(val_loss)
            history['train_mcc'].append(train_mcc)
            history['val_mcc'].append(val_mcc)
            history['lr'].append(optimizer.param_groups[0]['lr'])

            # Add to metrics records
            metrics_records.append({
                'epoch': epoch,
                'train_loss': train_loss,
                'val_loss': val_loss,
                'train_mcc': train_mcc,
                'val_mcc': val_mcc,
                'lr': optimizer.param_groups[0]['lr']
            })

            # Print epoch summary
            print(f"Epoch {epoch+1}/{num_epochs} - "
                  f"Train Loss: {train_loss:.4f}, MCC: {train_mcc:.4f} | "
                  f"Val Loss: {val_loss:.4f}, MCC: {val_mcc:.4f} | "
                  f"LR: {optimizer.param_groups[0]['lr']:.6f}")

            # Update ReduceLROnPlateau scheduler if used
            if scheduler_type == "reduce_on_plateau" and scheduler is not None:
                scheduler.step(val_mcc)

            # Report to Optuna for pruning only if enabled
            if report_to_optuna and trial is not None:
                trial.report(val_mcc, epoch)

                # Handle pruning based on val_mcc
                if trial.should_prune():
                    raise optuna.exceptions.TrialPruned()

            # Check early stopping
            best_val_mcc = early_stopping(val_mcc)
            if early_stopping.early_stop:
                print(f"\nEarly stopping triggered at epoch {epoch+1}. "
                      f"Best val MCC: {best_val_mcc:.4f}")
                break

    except Exception as e:
        if isinstance(e, optuna.exceptions.TrialPruned):
            print("Trial pruned by Optuna.")
            raise e
        else:
            print(f"Training error: {e}")

    # Create metrics DataFrame from collected records
    if metrics_records:
        metrics_df = pd.DataFrame(metrics_records)

    # Save metrics to CSV
    trial_id = trial.number if trial is not None else "final"
    metrics_path = os.path.join(RESULTS_DIR, "metrics") if metrics_dir is None else metrics_dir
    os.makedirs(metrics_path, exist_ok=True)
    metrics_df.to_csv(os.path.join(metrics_path, f"trial_{trial_id}_metrics.csv"), index=False)

    # Plot training history
    plot_training_history(history, trial_id)

    return history, best_val_mcc if early_stopping.best_metric is not None else val_mcc

In [ ]:
def plot_training_history(history, trial_id):
    """Plot training and validation loss and MCC over epochs."""
    # Ensure the plots directory exists
    plots_dir = os.path.join(RESULTS_DIR, "plots")
    os.makedirs(plots_dir, exist_ok=True)

    epochs = len(history['train_loss'])
    plt.figure(figsize=(15, 6))

    # Loss
    plt.subplot(1, 2, 1)
    plt.plot(range(1, epochs+1), history['train_loss'], label='Train Loss')
    plt.plot(range(1, epochs+1), history['val_loss'], label='Val Loss')
    plt.xlabel("Epoch")
    plt.ylabel("Loss")
    plt.title("Loss vs. Epochs")
    plt.legend()
    plt.grid(alpha=0.3)

    # MCC
    plt.subplot(1, 2, 2)
    plt.plot(range(1, epochs+1), history['train_mcc'], label='Train MCC')
    plt.plot(range(1, epochs+1), history['val_mcc'], label='Val MCC')
    plt.xlabel("Epoch")
    plt.ylabel("MCC")
    plt.title("MCC vs. Epochs")
    plt.legend()
    plt.grid(alpha=0.3)

    plt.tight_layout()

    # Save the plot
    plt.savefig(os.path.join(plots_dir, f"trial_{trial_id}_history.png"), dpi=300, bbox_inches='tight')
    plt.close()

    # Also save the data as CSV
    history_df = pd.DataFrame({
        'epoch': list(range(1, epochs+1)),
        'train_loss': history['train_loss'],
        'val_loss': history['val_loss'],
        'train_mcc': history['train_mcc'],
        'val_mcc': history['val_mcc'],
        'lr': history['lr']
    })
    history_df.to_csv(os.path.join(plots_dir, f"trial_{trial_id}_history.csv"), index=False)

def plot_confusion_matrix(conf_matrix, trial_id):
    """Plot confusion matrix."""
    plt.figure(figsize=(8, 7))
    sns.heatmap(conf_matrix, annot=True, fmt="d", cmap="Blues", cbar=False,
                xticklabels=['Predicted Negative', 'Predicted Positive'],
                yticklabels=['Actual Negative', 'Actual Positive'])
    plt.title("Confusion Matrix")
    plt.xlabel("Predicted Label")
    plt.ylabel("True Label")

    plt.savefig(os.path.join(RESULTS_DIR, f"plots/trial_{trial_id}_confusion_matrix.png"),
                dpi=300, bbox_inches='tight')
    plt.close()

    # Save confusion matrix data
    pd.DataFrame(conf_matrix).to_csv(
        os.path.join(RESULTS_DIR, f"plots/trial_{trial_id}_confusion_matrix.csv"),
        index=False
    )

def plot_roc_curve(all_labels, all_preds, trial_id):
    """Plot ROC curve."""
    fpr, tpr, _ = roc_curve(all_labels, all_preds)
    roc_auc = auc(fpr, tpr)

    plt.figure(figsize=(8, 7))
    plt.plot(fpr, tpr, color='darkorange', lw=2, label=f'ROC curve (area = {roc_auc:.3f})')
    plt.plot([0, 1], [0, 1], color='navy', lw=2, linestyle='--')
    plt.xlim([0.0, 1.0])
    plt.ylim([0.0, 1.05])
    plt.xlabel('False Positive Rate')
    plt.ylabel('True Positive Rate')
    plt.title('Receiver Operating Characteristic (ROC) Curve')
    plt.legend(loc="lower right")
    plt.grid(alpha=0.3)

    plt.savefig(os.path.join(RESULTS_DIR, f"plots/trial_{trial_id}_roc_curve.png"),
                dpi=300, bbox_inches='tight')
    plt.close()

    # Save ROC curve data
    pd.DataFrame({'fpr': fpr, 'tpr': tpr}).to_csv(
        os.path.join(RESULTS_DIR, f"plots/trial_{trial_id}_roc_curve.csv"),
        index=False
    )

def plot_pr_curve(all_labels, all_preds, trial_id):
    """Plot precision-recall curve."""
    precision_curve, recall_curve, _ = precision_recall_curve(all_labels, all_preds)
    pr_auc = auc(recall_curve, precision_curve)

    plt.figure(figsize=(8, 7))
    plt.plot(recall_curve, precision_curve, color='darkorange', lw=2,
             label=f'PR curve (area = {pr_auc:.3f})')
    plt.xlim([0.0, 1.0])
    plt.ylim([0.0, 1.05])
    plt.xlabel('Recall')
    plt.ylabel('Precision')
    plt.title('Precision-Recall Curve')
    plt.legend(loc="lower left")
    plt.grid(alpha=0.3)

    plt.savefig(os.path.join(RESULTS_DIR, f"plots/trial_{trial_id}_pr_curve.png"),
                dpi=300, bbox_inches='tight')
    plt.close()

    # Save PR curve data
    pd.DataFrame({'recall': recall_curve, 'precision': precision_curve}).to_csv(
        os.path.join(RESULTS_DIR, f"plots/trial_{trial_id}_pr_curve.csv"),
        index=False
    )

def visualize_optimization_history(study):
    """Visualize the optimization history."""
    try:
        # Plot optimization history
        fig = optuna.visualization.plot_optimization_history(study)
        fig.write_image(os.path.join(RESULTS_DIR, "optimization_history.png"))

        # Plot parameter importance
        fig = optuna.visualization.plot_param_importances(study)
        fig.write_image(os.path.join(RESULTS_DIR, "param_importances.png"))

        # Plot parallel coordinate
        fig = optuna.visualization.plot_parallel_coordinate(study)
        fig.write_image(os.path.join(RESULTS_DIR, "parallel_coordinate.png"))

        # Plot slice
        fig = optuna.visualization.plot_slice(study)
        fig.write_image(os.path.join(RESULTS_DIR, "slice_plot.png"))
    except:
        print("Error generating Optuna visualizations. Make sure plotly is installed.")
        print("You can install it with: pip install plotly kaleido")

    # Save study values
    study_df = study.trials_dataframe()
    study_df.to_csv(os.path.join(RESULTS_DIR, "study_results.csv"), index=False)

## Optuna Objective Function

In [ ]:
def objective_with_cv(trial, interactions_df, strain_embeddings, phage_embeddings, n_folds=5, random_state=42):
    """Optuna objective function with cross-validation for hyperparameter optimization."""
    # Sample hyperparameters
    pooling_type = trial.suggest_categorical("pooling_type", ["mean", "max", "median"])

    # Other hyperparameters remain the same
    classifier_hidden_layers = trial.suggest_int("classifier_hidden_layers", 1, 3)
    classifier_hidden_dim = trial.suggest_categorical("classifier_hidden_dim", [256, 384, 512, 768])
    dropout = trial.suggest_float("dropout", 0.05, 0.3)
    ln = trial.suggest_categorical("ln", [True, False])
    activation_function = trial.suggest_categorical("activation_function", ["relu", "gelu", "silu"])
    learning_rate = trial.suggest_float("learning_rate", 1e-5, 1e-4, log=True)
    batch_size = trial.suggest_categorical("batch_size", [128, 256, 512, 1024])
    use_phage_weights = trial.suggest_categorical("use_phage_weights", [True, False])
    weight_decay = trial.suggest_float("weight_decay", 0.001, 0.1, log=True)
    scheduler_type = trial.suggest_categorical(
        "scheduler_type",
        ["one_cycle", "cosine_annealing", "reduce_on_plateau"]
    )
    warmup_ratio = trial.suggest_float("warmup_ratio", 0.05, 0.2)

    # Print trial parameters
    print(f"\n{'='*80}")
    print(f"TRIAL {trial.number}: PARAMETER CONFIGURATION (WITH {n_folds}-FOLD CV)")
    print(f"{'='*80}")
    print("Architecture Parameters:")
    print(f"  - pooling_type: {pooling_type}")
    print(f"  - classifier_hidden_layers: {classifier_hidden_layers}")
    print(f"  - classifier_hidden_dim: {classifier_hidden_dim}")
    print(f"  - dropout: {dropout:.3f}")
    print(f"  - ln: {ln}")
    print(f"  - activation_function: {activation_function}")
    print("Training Parameters:")
    print(f"  - learning_rate: {learning_rate:.6f}")
    print(f"  - batch_size: {batch_size}")
    print(f"  - use_phage_weights: {use_phage_weights}")
    print(f"  - weight_decay: {weight_decay:.4f}")
    print(f"  - scheduler_type: {scheduler_type}")
    print(f"  - warmup_ratio: {warmup_ratio:.3f}")
    print(f"{'='*80}\n")

    # Setting patience based on num_epochs for early stopping
    num_epochs = 75  # Reduced from 100 since we'll be training multiple models
    patience = 7

    # Get unique strains for stratified sampling
    unique_strains = interactions_df['strain'].unique()

    # Create KFold object for splitting by strain
    from sklearn.model_selection import KFold
    kf = KFold(n_splits=n_folds, shuffle=True, random_state=random_state)

    # Store MCC values for each fold
    fold_mcc_values = []

    # Track all validation metrics across folds
    all_val_metrics = []

    # Loop through each fold
    for fold_idx, (train_idx, val_idx) in enumerate(kf.split(unique_strains)):
        print(f"\n{'='*80}")
        print(f"FOLD {fold_idx+1}/{n_folds}")
        print(f"{'='*80}")

        # Split strains into train and validation sets
        train_strains = unique_strains[train_idx]
        val_strains = unique_strains[val_idx]

        # Create dataframes based on strain splits
        train_df = interactions_df[interactions_df['strain'].isin(train_strains)]
        val_df = interactions_df[interactions_df['strain'].isin(val_strains)]

        print(f"Train set: {len(train_df)} interactions, {len(train_strains)} strains")
        print(f"Validation set: {len(val_df)} interactions, {len(val_strains)} strains")

        # Precompute pooled vectors
        pooled_strains, pooled_phages = precompute_pooled_embeddings(
            strain_embeddings, phage_embeddings, pooling_type
        )

        # Calculate phage-specific weights
        phage_weights = {}
        if use_phage_weights:
            phage_weights = calculate_phage_specific_weights(train_df)
        else:
            for phage in train_df['phage'].unique():
                phage_weights[phage] = 1.0

        # Create datasets with precomputed vectors
        train_dataset = PrecomputedPooledDataset(train_df, pooled_strains, pooled_phages, phage_weights)
        val_dataset = PrecomputedPooledDataset(val_df, pooled_strains, pooled_phages, phage_weights)

        # Create data loaders
        train_loader = torch.utils.data.DataLoader(
            train_dataset,
            batch_size=batch_size,
            shuffle=True,
            collate_fn=collate_pooled_vectors
        )

        val_loader = torch.utils.data.DataLoader(
            val_dataset,
            batch_size=batch_size,
            shuffle=False,
            collate_fn=collate_pooled_vectors
        )

        # Get embedding dimension from the first strain
        first_strain_id = next(iter(pooled_strains))
        embedding_dim = pooled_strains[first_strain_id].shape[0]

        # Initialize model
        model = PooledVectorModel(
            embedding_dim=embedding_dim,
            dropout=dropout,
            ln=ln,
            classifier_hidden_layers=classifier_hidden_layers,
            classifier_hidden_dim=classifier_hidden_dim,
            activation_function=activation_function
        ).to(device)

        # Train model
        history, val_mcc = train_model(
            model,
            train_loader,
            val_loader,
            trial,
            num_epochs=num_epochs,
            learning_rate=learning_rate,
            patience=patience,
            device=device,
            use_phage_weights=use_phage_weights,
            scheduler_type=scheduler_type,
            warmup_ratio=warmup_ratio,
            weight_decay=weight_decay,
            report_to_optuna=False  # Disable epoch-level reporting
        )

        # Evaluate on validation set
        val_metrics = evaluate_full(model, val_loader, device, use_phage_weights)
        all_val_metrics.append(val_metrics)

        # Store MCC value for this fold
        fold_mcc_values.append(val_mcc)

        print(f"Fold {fold_idx+1} - Val MCC: {val_mcc:.4f}")

        # Report to Optuna for pruning at fold level
        trial.report(val_mcc, fold_idx)

        # Handle pruning based on fold-level performance
        if trial.should_prune():
            raise optuna.exceptions.TrialPruned()

    # Calculate median and also mean/std of MCC across folds for reporting
    median_val_mcc = np.median(fold_mcc_values)
    mean_val_mcc = np.mean(fold_mcc_values)
    std_val_mcc = np.std(fold_mcc_values)

    # Print cross-validation results
    print(f"\n{'='*80}")
    print(f"CROSS-VALIDATION RESULTS")
    print(f"{'='*80}")
    print(f"Median MCC: {median_val_mcc:.4f}")
    print(f"Mean MCC: {mean_val_mcc:.4f} ± {std_val_mcc:.4f}")
    for fold_idx, fold_mcc in enumerate(fold_mcc_values):
        print(f"Fold {fold_idx+1} MCC: {fold_mcc:.4f}")
    print(f"{'='*80}\n")

    # Calculate median metrics across folds for more robust evaluation
    median_metrics = {
        'mcc': median_val_mcc,
        'accuracy': np.median([m['accuracy'] for m in all_val_metrics]),
        'precision': np.median([m['precision'] for m in all_val_metrics]),
        'recall': np.median([m['recall'] for m in all_val_metrics]),
        'f1': np.median([m['f1'] for m in all_val_metrics]),
        'roc_auc': np.median([m['roc_auc'] for m in all_val_metrics]),
        'pr_auc': np.median([m['pr_auc'] for m in all_val_metrics])
    }

    # Also calculate mean metrics for comparison
    mean_metrics = {
        'mcc': mean_val_mcc,
        'accuracy': np.mean([m['accuracy'] for m in all_val_metrics]),
        'precision': np.mean([m['precision'] for m in all_val_metrics]),
        'recall': np.mean([m['recall'] for m in all_val_metrics]),
        'f1': np.mean([m['f1'] for m in all_val_metrics]),
        'roc_auc': np.mean([m['roc_auc'] for m in all_val_metrics]),
        'pr_auc': np.mean([m['pr_auc'] for m in all_val_metrics])
    }

    # Log trial results
    trial_report = {
        'trial_number': trial.number,
        'val_mcc_median': median_val_mcc,
        'val_mcc_mean': mean_val_mcc,
        'val_mcc_std': std_val_mcc,
        'val_mcc_per_fold': fold_mcc_values,
        'median_metrics': median_metrics,
        'mean_metrics': mean_metrics,
        'hyperparameters': {
            'pooling_type': pooling_type,
            'dropout': dropout,
            'ln': ln,
            'classifier_hidden_layers': classifier_hidden_layers,
            'classifier_hidden_dim': classifier_hidden_dim,
            'activation_function': activation_function,
            'learning_rate': learning_rate,
            'batch_size': batch_size,
            'use_phage_weights': use_phage_weights,
            'weight_decay': weight_decay,
            'scheduler_type': scheduler_type,
            'warmup_ratio': warmup_ratio
        }
    }

    # Save trial report
    with open(os.path.join(RESULTS_DIR, f"trial_{trial.number}_report.pkl"), 'wb') as f:
        pickle.dump(trial_report, f)

    # Return median MCC as optimization metric
    return median_val_mcc

def train_best_model_with_multiple_seeds(study, interactions_df, strain_embeddings, phage_embeddings,
                                         n_seeds=5, random_state_base=42):
    """
    Train the best model from the CV study multiple times with different random seeds.
    Uses median for more robust performance estimation.
    """
    best_params = study.best_trial.params

    print(f"\n{'='*80}")
    print(f"TRAINING FINAL MODEL WITH {n_seeds} DIFFERENT RANDOM SEEDS")
    print(f"{'='*80}")

    # Store metrics for each seed
    all_seed_metrics = []
    all_models = []

    for seed_idx in range(n_seeds):
        random_state = random_state_base + seed_idx
        print(f"\n{'='*80}")
        print(f"SEED {seed_idx+1}/{n_seeds} (random_state={random_state})")
        print(f"{'='*80}")

        # Split data with current seed
        train_df, test_df = filter_interactions_by_strain(interactions_df, random_state)

        # Precompute pooled vectors with the best pooling type
        pooled_strains, pooled_phages = precompute_pooled_embeddings(
            strain_embeddings, phage_embeddings, pooling_type=best_params['pooling_type']
        )

        # Calculate phage-specific weights if needed
        phage_weights = {}
        if best_params['use_phage_weights']:
            phage_weights = calculate_phage_specific_weights(train_df)
        else:
            for phage in train_df['phage'].unique():
                phage_weights[phage] = 1.0

        # Create datasets
        train_dataset = PrecomputedPooledDataset(train_df, pooled_strains, pooled_phages, phage_weights)
        test_dataset = PrecomputedPooledDataset(test_df, pooled_strains, pooled_phages, phage_weights)

        # Create dataloaders
        train_loader = torch.utils.data.DataLoader(
            train_dataset,
            batch_size=best_params['batch_size'],
            shuffle=True,
            collate_fn=collate_pooled_vectors
        )

        test_loader = torch.utils.data.DataLoader(
            test_dataset,
            batch_size=best_params['batch_size'],
            shuffle=False,
            collate_fn=collate_pooled_vectors
        )

        # Get embedding dimension from the first strain
        first_strain_id = next(iter(pooled_strains))
        embedding_dim = pooled_strains[first_strain_id].shape[0]

        # Initialize model with best parameters
        model = PooledVectorModel(
            embedding_dim=embedding_dim,
            dropout=best_params['dropout'],
            ln=best_params['ln'],
            classifier_hidden_layers=best_params['classifier_hidden_layers'],
            classifier_hidden_dim=best_params['classifier_hidden_dim'],
            activation_function=best_params['activation_function']
        ).to(device)

        # Train the model
        history, val_mcc = train_model(
            model,
            train_loader,
            test_loader,
            None,  # No trial object for final training
            num_epochs=150,  # Use more epochs for final model
            learning_rate=best_params['learning_rate'],
            patience=15,  # More patience for final model
            device=device,
            use_phage_weights=best_params['use_phage_weights'],
            scheduler_type=best_params['scheduler_type'],
            warmup_ratio=best_params['warmup_ratio'],
            weight_decay=best_params['weight_decay']
        )

        # Evaluate on test set
        test_metrics = evaluate_full(model, test_loader, device, best_params['use_phage_weights'])
        all_seed_metrics.append(test_metrics)
        all_models.append(model)

        # Save this seed's model
        torch.save({
            'model_state_dict': model.state_dict(),
            'best_params': best_params,
            'test_metrics': test_metrics,
            'seed': random_state,
            'embedding_dim': embedding_dim
        }, os.path.join(RESULTS_DIR, f"models/final_model_seed_{random_state}.pt"))

        # Print seed results
        print(f"\nSeed {seed_idx+1} performance:")
        print(f"Test MCC: {test_metrics['mcc']:.4f}")
        print(f"Test Accuracy: {test_metrics['accuracy']:.4f}")
        print(f"Test F1: {test_metrics['f1']:.4f}")
        print(f"Test ROC AUC: {test_metrics['roc_auc']:.4f}")
        print(f"Test PR AUC: {test_metrics['pr_auc']:.4f}")

    # Calculate median metrics across seeds
    median_mcc = np.median([m['mcc'] for m in all_seed_metrics])
    median_accuracy = np.median([m['accuracy'] for m in all_seed_metrics])
    median_f1 = np.median([m['f1'] for m in all_seed_metrics])
    median_roc_auc = np.median([m['roc_auc'] for m in all_seed_metrics])
    median_pr_auc = np.median([m['pr_auc'] for m in all_seed_metrics])

    # Also calculate mean and std for comparison
    mean_mcc = np.mean([m['mcc'] for m in all_seed_metrics])
    std_mcc = np.std([m['mcc'] for m in all_seed_metrics])

    # Find the best seed model based on MCC
    best_seed_idx = np.argmax([m['mcc'] for m in all_seed_metrics])
    best_seed = random_state_base + best_seed_idx
    best_model = all_models[best_seed_idx]
    best_metrics = all_seed_metrics[best_seed_idx]

    # Also identify the median model (closest to median MCC)
    median_seed_idx = np.argmin(np.abs(np.array([m['mcc'] for m in all_seed_metrics]) - median_mcc))
    median_seed = random_state_base + median_seed_idx
    median_model = all_models[median_seed_idx]
    median_seed_metrics = all_seed_metrics[median_seed_idx]

    # Save both the best model and the median model
    # Best model (highest MCC)
    torch.save({
        'model_state_dict': best_model.state_dict(),
        'best_params': best_params,
        'test_metrics': best_metrics,
        'seed': best_seed,
        'embedding_dim': embedding_dim,
        'all_seed_metrics': all_seed_metrics,
        'median_mcc': median_mcc,
        'mean_mcc': mean_mcc,
        'std_mcc': std_mcc,
        'selection_criterion': 'best_mcc'
    }, os.path.join(RESULTS_DIR, "models/final_model_best.pt"))

    # Median model (closest to median MCC)
    torch.save({
        'model_state_dict': median_model.state_dict(),
        'best_params': best_params,
        'test_metrics': median_seed_metrics,
        'seed': median_seed,
        'embedding_dim': embedding_dim,
        'all_seed_metrics': all_seed_metrics,
        'median_mcc': median_mcc,
        'mean_mcc': mean_mcc,
        'std_mcc': std_mcc,
        'selection_criterion': 'median_mcc'
    }, os.path.join(RESULTS_DIR, "models/final_model_median.pt"))

    # Print final results summary
    print(f"\n{'='*80}")
    print(f"FINAL MODEL SUMMARY ({n_seeds} SEEDS)")
    print(f"{'='*80}")
    print(f"Median Test MCC: {median_mcc:.4f}")
    print(f"Mean Test MCC: {mean_mcc:.4f} ± {std_mcc:.4f}")
    print(f"Median Test Accuracy: {median_accuracy:.4f}")
    print(f"Median Test F1: {median_f1:.4f}")
    print(f"Median Test ROC AUC: {median_roc_auc:.4f}")
    print(f"Median Test PR AUC: {median_pr_auc:.4f}")

    print(f"\nBest model (seed {best_seed}):")
    print(f"Test MCC: {best_metrics['mcc']:.4f}")
    print(f"Test Accuracy: {best_metrics['accuracy']:.4f}")
    print(f"Test F1: {best_metrics['f1']:.4f}")

    print(f"\nMedian model (seed {median_seed}):")
    print(f"Test MCC: {median_seed_metrics['mcc']:.4f}")
    print(f"Test Accuracy: {median_seed_metrics['accuracy']:.4f}")
    print(f"Test F1: {median_seed_metrics['f1']:.4f}")

    print(f"{'='*80}")

    # Save summary report
    final_report = {
        'best_params': best_params,
        'all_seed_metrics': all_seed_metrics,
        'median_metrics': {
            'mcc': median_mcc,
            'accuracy': median_accuracy,
            'f1': median_f1,
            'roc_auc': median_roc_auc,
            'pr_auc': median_pr_auc
        },
        'mean_metrics': {
            'mcc': mean_mcc,
            'accuracy': np.mean([m['accuracy'] for m in all_seed_metrics]),
            'f1': np.mean([m['f1'] for m in all_seed_metrics]),
            'roc_auc': np.mean([m['roc_auc'] for m in all_seed_metrics]),
            'pr_auc': np.mean([m['pr_auc'] for m in all_seed_metrics])
        },
        'std_metrics': {
            'mcc': std_mcc,
            'accuracy': np.std([m['accuracy'] for m in all_seed_metrics]),
            'f1': np.std([m['f1'] for m in all_seed_metrics]),
            'roc_auc': np.std([m['roc_auc'] for m in all_seed_metrics]),
            'pr_auc': np.std([m['pr_auc'] for m in all_seed_metrics])
        },
        'best_seed': best_seed,
        'best_metrics': best_metrics,
        'median_seed': median_seed,
        'median_seed_metrics': median_seed_metrics,
        'n_seeds': n_seeds
    }

    with open(os.path.join(RESULTS_DIR, "final_model_multiple_seeds_report.pkl"), 'wb') as f:
        pickle.dump(final_report, f)

    # Return both models and the report
    return best_model, median_model, final_report

## Run Optimization

In [ ]:
def run_optimization(interactions_path, strain_embeddings_path, phage_embeddings_path,
                    n_trials=50, random_state=42, study_name=None, output_dir=None,
                    n_folds=5, n_final_seeds=5):
    """Run optimization with cross-validation and multiple seeds for final model."""
    # Set global RESULTS_DIR
    global RESULTS_DIR

    # Always generate a timestamp for record-keeping
    timestamp = datetime.datetime.now().strftime("%Y%m%d_%H%M%S")

    # Use custom output_dir if provided, otherwise create timestamped directory
    if output_dir:
        RESULTS_DIR = output_dir
    else:
        RESULTS_DIR = f"optuna_pooling_cv_results_{timestamp}"

    # Create directory structure
    os.makedirs(RESULTS_DIR, exist_ok=True)
    os.makedirs(os.path.join(RESULTS_DIR, "plots"), exist_ok=True)
    os.makedirs(os.path.join(RESULTS_DIR, "models"), exist_ok=True)
    os.makedirs(os.path.join(RESULTS_DIR, "metrics"), exist_ok=True)

    print("\n" + "="*80)
    print(f"Starting hyperparameter optimization with {n_trials} trials")
    print(f"Using {n_folds}-fold cross-validation")
    print(f"Final model will be trained with {n_final_seeds} different seeds")
    print("="*80)
    print(f"Interactions file: {interactions_path}")
    print(f"Strain embeddings: {strain_embeddings_path}")
    print(f"Phage embeddings: {phage_embeddings_path}")
    print(f"Results directory: {RESULTS_DIR}")
    print("="*80 + "\n")

    # Save configuration
    config = {
        'interactions_path': interactions_path,
        'strain_embeddings_path': strain_embeddings_path,
        'phage_embeddings_path': phage_embeddings_path,
        'n_trials': n_trials,
        'random_state': random_state,
        'study_name': study_name,
        'timestamp': timestamp,
        'results_dir': RESULTS_DIR,
        'n_folds': n_folds,
        'n_final_seeds': n_final_seeds
    }

    with open(os.path.join(RESULTS_DIR, "config.json"), 'w') as f:
        json.dump(config, f, indent=4)

    # 1. Load data
    print("Loading embeddings...")
    strain_embeddings = load_embeddings_flexible(strain_embeddings_path)
    phage_embeddings = load_embeddings_flexible(phage_embeddings_path)

    print("Loading interaction data...")
    interactions_df = pd.read_csv(interactions_path)

    # 2. Filter to ensure we have embeddings for all strains/phages
    strain_keys = set(strain_embeddings.keys())
    phage_keys = set(phage_embeddings.keys())

    filtered_df = interactions_df[
        interactions_df['strain'].isin(strain_keys) &
        interactions_df['phage'].isin(phage_keys)
    ]

    print(f"Original interactions: {len(interactions_df)}")
    print(f"Filtered interactions: {len(filtered_df)}")

    if len(filtered_df) == 0:
        raise ValueError("No interactions match the provided embeddings!")

    # 3. Configure the study with database storage for resumability
    DB_PATH = os.path.join(RESULTS_DIR, "optuna_study_cv.db")
    storage = optuna.storages.RDBStorage(f"sqlite:///{DB_PATH}")

    # Create or load study (for resumability)
    try:
        study = optuna.load_study(
            study_name=study_name if study_name else f"cv_study_{timestamp}",
            storage=storage
        )
        print(f"Resuming existing study '{study_name}' with {len(study.trials)} completed trials")
        remaining_trials = max(0, n_trials - len(study.trials))
    except:
        study = optuna.create_study(
            study_name=study_name if study_name else f"cv_study_{timestamp}",
            direction="maximize",
            sampler=TPESampler(seed=random_state),
            pruner=MedianPruner(n_startup_trials=5, n_warmup_steps=10),
            storage=storage
        )
        print(f"Created new study '{study_name}' with {n_folds}-fold cross-validation")
        remaining_trials = n_trials

    # 4. Create objective function with cross-validation
    objective_func = lambda trial: objective_with_cv(
        trial, filtered_df, strain_embeddings, phage_embeddings, n_folds, random_state
    )

    if remaining_trials > 0:
        # 5. Run optimization
        study.optimize(objective_func, n_trials=remaining_trials)

        # 6. Print study statistics
        print("\nStudy completed!")
        print(f"Number of finished trials: {len(study.trials)}")
        print("Best trial:")
        best_trial = study.best_trial
        print(f"  Value (median MCC): {best_trial.value:.4f}")
        print("  Params:")
        for key, value in best_trial.params.items():
            print(f"    {key}: {value}")

        # 7. Visualize study
        print("\nCreating visualization plots...")
        visualize_optimization_history(study)
    else:
        print("All trials already completed, skipping optimization.")

    # 8. Train the best model with multiple seeds
    print(f"\nTraining the best model with {n_final_seeds} different seeds...")
    best_model, median_model, final_report = train_best_model_with_multiple_seeds(
        study, filtered_df, strain_embeddings, phage_embeddings,
        n_seeds=n_final_seeds, random_state_base=random_state
    )

    # 9. Save the final study results
    trials_df = study.trials_dataframe()
    trials_df.to_csv(os.path.join(RESULTS_DIR, "all_trials_results_cv.csv"), index=False)

    # Save best parameters in a more accessible format
    best_params = study.best_params
    with open(os.path.join(RESULTS_DIR, "best_params_cv.json"), 'w') as f:
        json.dump(best_params, f, indent=4)

    print(f"\nAll study artifacts saved to {RESULTS_DIR}")

    # Print final model performance summary
    print("\nFinal Model Performance Summary:")
    print(f"Best model MCC: {final_report['best_metrics']['mcc']:.4f}")
    print(f"Median model MCC: {final_report['median_seed_metrics']['mcc']:.4f}")
    print(f"Median MCC across all seeds: {final_report['median_metrics']['mcc']:.4f}")
    print(f"Mean MCC across all seeds: {final_report['mean_metrics']['mcc']:.4f} ± {final_report['std_metrics']['mcc']:.4f}")

    return study, best_model, median_model, final_report

## Main Section

In [ ]:
# E. coli dataset paths (uncomment and modify as needed)
interactions_path = '/content/drive/MyDrive/Arkin/phage_public_datasets/e_coli/interaction_matrix.csv'
strain_embeddings_path = '/content/drive/MyDrive/Arkin/set_transformer_data/embedding_experiments/ecoli/current_embeddings/strain'
phage_embeddings_path = '/content/drive/MyDrive/Arkin/set_transformer_data/embedding_experiments/ecoli/current_embeddings/phage'
output_dir = "/content/drive/MyDrive/Arkin/set_transformer_data/glm_optuna_pooling_cv"

# EDGE dataset paths (uncomment and modify as needed)
# interactions_path = '/content/drive/MyDrive/Arkin/set_transformer_data/EDGE_interaction_long_172_no2.csv'
# strain_embeddings_path = '/content/drive/MyDrive/Arkin/set_transformer_data/embedding_sets/strains'
# phage_embeddings_path = '/content/drive/MyDrive/Arkin/set_transformer_data/embedding_sets/phages'

if __name__ == "__main__":
    study, best_model, median_model, final_report = run_optimization(
        interactions_path=interactions_path,
        strain_embeddings_path=strain_embeddings_path,
        phage_embeddings_path=phage_embeddings_path,
        n_trials=250,
        study_name='glm_optuna_pooling_cv',
        output_dir=output_dir,
        n_folds=5,       # Number of cross-validation folds
        n_final_seeds=5  # Number of seeds for final model training
    )

    # Display a nice summary of the results
    best_trial = study.best_trial
    print(f"Best trial value (MCC): {best_trial.value:.4f}")
    print("Best parameters:")
    for key, value in best_trial.params.items():
        print(f"  {key}: {value}")

    # print("Run the optimization by uncommenting and setting the correct paths in the main section!")


Starting hyperparameter optimization with 250 trials
Using 5-fold cross-validation
Final model will be trained with 5 different seeds
Interactions file: /content/drive/MyDrive/Arkin/phage_public_datasets/e_coli/interaction_matrix.csv
Strain embeddings: /content/drive/MyDrive/Arkin/set_transformer_data/embedding_experiments/ecoli/current_embeddings/strain
Phage embeddings: /content/drive/MyDrive/Arkin/set_transformer_data/embedding_experiments/ecoli/current_embeddings/phage
Results directory: /content/drive/MyDrive/Arkin/set_transformer_data/glm_optuna_pooling_cv

Loading embeddings...
Successfully loaded 177 embeddings
Successfully loaded 97 embeddings
Loading interaction data...
Original interactions: 38592
Filtered interactions: 16992


[I 2025-04-22 05:21:51,684] A new study created in RDB with name: glm_optuna_pooling_cv


Created new study 'glm_optuna_pooling_cv' with 5-fold cross-validation

TRIAL 0: PARAMETER CONFIGURATION (WITH 5-FOLD CV)
Architecture Parameters:
  - pooling_type: max
  - classifier_hidden_layers: 2
  - classifier_hidden_dim: 768
  - dropout: 0.200
  - ln: True
  - activation_function: relu
Training Parameters:
  - learning_rate: 0.000015
  - batch_size: 512
  - use_phage_weights: False
  - weight_decay: 0.0019
  - scheduler_type: reduce_on_plateau
  - warmup_ratio: 0.168


FOLD 1/5
Train set: 13536 interactions, 141 strains
Validation set: 3456 interactions, 36 strains
Precomputing max pooling for 177 strains...
Precomputing max pooling for 97 phages...
Epoch 1/75 - Train Loss: 0.5833, MCC: -0.0057 | Val Loss: 0.5177, MCC: 0.0000 | LR: 0.000015
Epoch 2/75 - Train Loss: 0.5366, MCC: 0.0000 | Val Loss: 0.4997, MCC: 0.0000 | LR: 0.000015
Epoch 3/75 - Train Loss: 0.5274, MCC: 0.0007 | Val Loss: 0.4906, MCC: 0.0000 | LR: 0.000015
Epoch 4/75 - Train Loss: 0.5160, MCC: 0.0260 | Val Loss: 0

[I 2025-04-22 05:26:30,450] Trial 0 finished with value: 0.28451214388165563 and parameters: {'pooling_type': 'max', 'classifier_hidden_layers': 2, 'classifier_hidden_dim': 768, 'dropout': 0.20027875293580222, 'ln': True, 'activation_function': 'relu', 'learning_rate': 1.5199348301309802e-05, 'batch_size': 512, 'use_phage_weights': False, 'weight_decay': 0.0019010245319870357, 'scheduler_type': 'reduce_on_plateau', 'warmup_ratio': 0.16777639420895207}. Best is trial 0 with value: 0.28451214388165563.


Fold 5 - Val MCC: 0.2804

CROSS-VALIDATION RESULTS
Median MCC: 0.2845
Mean MCC: 0.2736 ± 0.0241
Fold 1 MCC: 0.2887
Fold 2 MCC: 0.2845
Fold 3 MCC: 0.2257
Fold 4 MCC: 0.2884
Fold 5 MCC: 0.2804


TRIAL 1: PARAMETER CONFIGURATION (WITH 5-FOLD CV)
Architecture Parameters:
  - pooling_type: median
  - classifier_hidden_layers: 1
  - classifier_hidden_dim: 768
  - dropout: 0.291
  - ln: True
  - activation_function: gelu
Training Parameters:
  - learning_rate: 0.000013
  - batch_size: 512
  - use_phage_weights: True
  - weight_decay: 0.0110
  - scheduler_type: reduce_on_plateau
  - warmup_ratio: 0.166


FOLD 1/5
Train set: 13536 interactions, 141 strains
Validation set: 3456 interactions, 36 strains
Precomputing median pooling for 177 strains...
Precomputing median pooling for 97 phages...
Epoch 1/75 - Train Loss: 0.9944, MCC: 0.0404 | Val Loss: 0.9308, MCC: -0.0141 | LR: 0.000013
Epoch 2/75 - Train Loss: 0.9891, MCC: 0.0562 | Val Loss: 0.9177, MCC: 0.0550 | LR: 0.000013
Epoch 3/75 - Train Lo

...

Fold 5 - Val MCC: 0.3258

CROSS-VALIDATION RESULTS
Median MCC: 0.3269
Mean MCC: 0.3143 ± 0.0309
Fold 1 MCC: 0.3301
Fold 2 MCC: 0.3269
Fold 3 MCC: 0.3355
Fold 4 MCC: 0.2528
Fold 5 MCC: 0.3258


TRIAL 248: PARAMETER CONFIGURATION (WITH 5-FOLD CV)
Architecture Parameters:
  - pooling_type: mean
  - classifier_hidden_layers: 3
  - classifier_hidden_dim: 512
  - dropout: 0.122
  - ln: True
  - activation_function: relu
Training Parameters:
  - learning_rate: 0.000051
  - batch_size: 512
  - use_phage_weights: False
  - weight_decay: 0.0136
  - scheduler_type: cosine_annealing
  - warmup_ratio: 0.186


FOLD 1/5
Train set: 13536 interactions, 141 strains
Validation set: 3456 interactions, 36 strains
Precomputing mean pooling for 177 strains...
Precomputing mean pooling for 97 phages...
Epoch 1/75 - Train Loss: 0.5360, MCC: -0.0020 | Val Loss: 0.4773, MCC: 0.0000 | LR: 0.000051
Epoch 2/75 - Train Loss: 0.5131, MCC: 0.0416 | Val Loss: 0.4659, MCC: 0.0000 | LR: 0.000051
Epoch 3/75 - Train Loss: 

[I 2025-04-22 23:27:22,649] Trial 248 finished with value: 0.3301495479532531 and parameters: {'pooling_type': 'mean', 'classifier_hidden_layers': 3, 'classifier_hidden_dim': 512, 'dropout': 0.12202233244434393, 'ln': True, 'activation_function': 'relu', 'learning_rate': 5.070255956347065e-05, 'batch_size': 512, 'use_phage_weights': False, 'weight_decay': 0.013610580312042764, 'scheduler_type': 'cosine_annealing', 'warmup_ratio': 0.18639925287866338}. Best is trial 184 with value: 0.3355107650026586.


Fold 5 - Val MCC: 0.3276

CROSS-VALIDATION RESULTS
Median MCC: 0.3301
Mean MCC: 0.3243 ± 0.0185
Fold 1 MCC: 0.3301
Fold 2 MCC: 0.3400
Fold 3 MCC: 0.3355
Fold 4 MCC: 0.2883
Fold 5 MCC: 0.3276


TRIAL 249: PARAMETER CONFIGURATION (WITH 5-FOLD CV)
Architecture Parameters:
  - pooling_type: mean
  - classifier_hidden_layers: 3
  - classifier_hidden_dim: 384
  - dropout: 0.149
  - ln: True
  - activation_function: relu
Training Parameters:
  - learning_rate: 0.000065
  - batch_size: 512
  - use_phage_weights: False
  - weight_decay: 0.0287
  - scheduler_type: cosine_annealing
  - warmup_ratio: 0.181


FOLD 1/5
Train set: 13536 interactions, 141 strains
Validation set: 3456 interactions, 36 strains
Precomputing mean pooling for 177 strains...
Precomputing mean pooling for 97 phages...
Epoch 1/75 - Train Loss: 0.5511, MCC: -0.0014 | Val Loss: 0.5003, MCC: 0.0000 | LR: 0.000065
Epoch 2/75 - Train Loss: 0.5198, MCC: 0.0036 | Val Loss: 0.4702, MCC: 0.0000 | LR: 0.000065
Epoch 3/75 - Train Loss: 

[I 2025-04-22 23:30:25,437] Trial 249 finished with value: 0.3167103185618868 and parameters: {'pooling_type': 'mean', 'classifier_hidden_layers': 3, 'classifier_hidden_dim': 384, 'dropout': 0.14942668504255233, 'ln': True, 'activation_function': 'relu', 'learning_rate': 6.461472911895777e-05, 'batch_size': 512, 'use_phage_weights': False, 'weight_decay': 0.028664522261363165, 'scheduler_type': 'cosine_annealing', 'warmup_ratio': 0.18124751752257026}. Best is trial 184 with value: 0.3355107650026586.


Fold 5 - Val MCC: 0.3167

CROSS-VALIDATION RESULTS
Median MCC: 0.3167
Mean MCC: 0.3087 ± 0.0228
Fold 1 MCC: 0.3301
Fold 2 MCC: 0.3276
Fold 3 MCC: 0.3014
Fold 4 MCC: 0.2679
Fold 5 MCC: 0.3167


Study completed!
Number of finished trials: 250
Best trial:
  Value (median MCC): 0.3355
  Params:
    pooling_type: mean
    classifier_hidden_layers: 3
    classifier_hidden_dim: 512
    dropout: 0.1399261039732264
    ln: True
    activation_function: relu
    learning_rate: 5.924978444690761e-05
    batch_size: 512
    use_phage_weights: False
    weight_decay: 0.033737044834691504
    scheduler_type: cosine_annealing
    warmup_ratio: 0.18417067616941543

Creating visualization plots...

Training the best model with 5 different seeds...

TRAINING FINAL MODEL WITH 5 DIFFERENT RANDOM SEEDS

SEED 1/5 (random_state=42)
Train set: 13536 interactions, 141 strains
Test set:  3456 interactions, 36 strains
Precomputing mean pooling for 177 strains...
Precomputing mean pooling for 97 phages...
Epoch 1

In [ ]:
def generate_plots_for_saved_model(
    results_dir,
    model_name,
    interactions_path,
    strain_embeddings_path,
    phage_embeddings_path,
    output_dir=None
):
    """
    Generate confusion matrix, ROC curve, and PR curve for a saved model.

    Args:
        results_dir: Base directory where models are stored
        model_name: Name of model ('best', 'median', or specific seed 42-46)
        interactions_path: Path to interactions CSV
        strain_embeddings_path: Path to strain embeddings directory
        phage_embeddings_path: Path to phage embeddings directory
        output_dir: Directory to save the plots
    """
    import os
    import numpy as np
    import pandas as pd
    import torch
    import matplotlib.pyplot as plt
    import seaborn as sns
    from sklearn.metrics import (
        confusion_matrix, roc_curve, precision_recall_curve, auc,
        accuracy_score, precision_score, recall_score, f1_score, matthews_corrcoef
    )

    # Set up output directory
    if output_dir is None:
        output_dir = os.path.join(results_dir, "plots", f"model_{model_name}")
    os.makedirs(output_dir, exist_ok=True)

    # Format model name properly
    if model_name.lower() in ['best', 'median']:
        model_filename = f"final_model_{model_name.lower()}.pt"
    elif model_name.isdigit() or (isinstance(model_name, int)):
        model_filename = f"final_model_seed_{model_name}.pt"
    else:
        model_filename = model_name  # In case the full filename was provided

    # Construct model path
    model_path = os.path.join(results_dir, "models", model_filename)

    # Check if model exists
    if not os.path.exists(model_path):
        raise ValueError(f"Model not found at {model_path}")

    # Load the model with weights_only=False to handle the error
    print(f"Loading model from {model_path}")
    try:
        # First try loading normally
        checkpoint = torch.load(model_path, map_location='cpu')
    except Exception as e:
        print(f"Error loading model: {e}")
        print("Trying with weights_only=False...")
        # Try with weights_only=False
        checkpoint = torch.load(model_path, map_location='cpu', weights_only=False)

    # Get random state and parameters from the checkpoint
    random_state = checkpoint.get('seed', 42)
    params = checkpoint.get('best_params', {})
    print(f"Using seed {random_state} and {params.get('pooling_type', 'mean')} pooling")

    # Import the necessary functions from the original script
    # from mean_pooling_optuna_glm_cv import (
    #     load_embeddings_flexible, filter_interactions_by_strain,
    #     precompute_pooled_embeddings, PooledVectorModel
    # )

    # Load the data
    print("Loading embeddings and interaction data...")
    strain_embeddings = load_embeddings_flexible(strain_embeddings_path)
    phage_embeddings = load_embeddings_flexible(phage_embeddings_path)
    interactions_df = pd.read_csv(interactions_path)

    # Filter to ensure we have embeddings for all strains/phages
    strain_keys = set(strain_embeddings.keys())
    phage_keys = set(phage_embeddings.keys())

    filtered_df = interactions_df[
        interactions_df['strain'].isin(strain_keys) &
        interactions_df['phage'].isin(phage_keys)
    ]

    print(f"Using {len(filtered_df)} interactions")

    # Split data using same random state as original
    train_df, test_df = filter_interactions_by_strain(filtered_df, random_state)
    print(f"Test set size: {len(test_df)} interactions")

    # Precompute pooled vectors using the same pooling method
    pooling_type = params.get('pooling_type', 'mean')
    pooled_strains, pooled_phages = precompute_pooled_embeddings(
        strain_embeddings, phage_embeddings, pooling_type
    )

    # Reconstruct the model with the saved architecture
    first_strain_id = next(iter(pooled_strains))
    embedding_dim = pooled_strains[first_strain_id].shape[0]
    model = PooledVectorModel(
        embedding_dim=embedding_dim,
        dropout=params.get('dropout', 0.1),
        ln=params.get('ln', True),
        classifier_hidden_layers=params.get('classifier_hidden_layers', 1),
        classifier_hidden_dim=params.get('classifier_hidden_dim', None),
        activation_function=params.get('activation_function', "relu")
    )

    # Load the model weights
    model.load_state_dict(checkpoint['model_state_dict'])
    model.eval()

    # Generate predictions
    print("Generating predictions on test data...")
    all_preds = []
    all_labels = []
    all_strains = []
    all_phages = []

    # Batch process the test data
    for _, row in test_df.iterrows():
        strain_id = row['strain']
        phage_id = row['phage']
        label = row['interaction']

        # Get pooled vectors
        strain_vec = torch.tensor(pooled_strains[strain_id], dtype=torch.float32).unsqueeze(0)
        phage_vec = torch.tensor(pooled_phages[phage_id], dtype=torch.float32).unsqueeze(0)

        # Get prediction
        with torch.no_grad():
            logit = model(strain_vec, phage_vec)
            pred = torch.sigmoid(logit).item()

        all_preds.append(pred)
        all_labels.append(label)
        all_strains.append(strain_id)
        all_phages.append(phage_id)

    # Convert to numpy arrays
    all_preds = np.array(all_preds)
    all_labels = np.array(all_labels)

    # Generate binary predictions
    binary_preds = (all_preds > 0.5).astype(int)

    # Calculate confusion matrix
    conf_matrix = confusion_matrix(all_labels, binary_preds)

    # 1. Plot confusion matrix
    plt.figure(figsize=(8, 7))
    sns.heatmap(conf_matrix, annot=True, fmt="d", cmap="Blues", cbar=False,
                xticklabels=['Predicted Negative', 'Predicted Positive'],
                yticklabels=['Actual Negative', 'Actual Positive'])
    plt.title(f"Confusion Matrix (Model: {model_name})")
    plt.xlabel("Predicted Label")
    plt.ylabel("True Label")
    plt.savefig(os.path.join(output_dir, f"model_{model_name}_confusion_matrix.png"),
                dpi=300, bbox_inches='tight')
    plt.close()

    # Save confusion matrix data
    pd.DataFrame(conf_matrix,
                 columns=['Predicted Negative', 'Predicted Positive'],
                 index=['Actual Negative', 'Actual Positive']).to_csv(
        os.path.join(output_dir, f"model_{model_name}_confusion_matrix.csv")
    )

    # 2. Plot ROC curve
    fpr, tpr, _ = roc_curve(all_labels, all_preds)
    roc_auc = auc(fpr, tpr)

    plt.figure(figsize=(8, 7))
    plt.plot(fpr, tpr, color='darkorange', lw=2, label=f'ROC curve (area = {roc_auc:.3f})')
    plt.plot([0, 1], [0, 1], color='navy', lw=2, linestyle='--')
    plt.xlim([0.0, 1.0])
    plt.ylim([0.0, 1.05])
    plt.xlabel('False Positive Rate')
    plt.ylabel('True Positive Rate')
    plt.title(f'ROC Curve (Model: {model_name})')
    plt.legend(loc="lower right")
    plt.grid(alpha=0.3)
    plt.savefig(os.path.join(output_dir, f"model_{model_name}_roc_curve.png"),
                dpi=300, bbox_inches='tight')
    plt.close()

    # Save ROC curve data
    pd.DataFrame({'fpr': fpr, 'tpr': tpr}).to_csv(
        os.path.join(output_dir, f"model_{model_name}_roc_curve.csv"),
        index=False
    )

    # 3. Plot PR curve
    precision_curve, recall_curve, _ = precision_recall_curve(all_labels, all_preds)
    pr_auc = auc(recall_curve, precision_curve)

    plt.figure(figsize=(8, 7))
    plt.plot(recall_curve, precision_curve, color='darkorange', lw=2,
             label=f'PR curve (area = {pr_auc:.3f})')
    plt.xlim([0.0, 1.0])
    plt.ylim([0.0, 1.05])
    plt.xlabel('Recall')
    plt.ylabel('Precision')
    plt.title(f'Precision-Recall Curve (Model: {model_name})')
    plt.legend(loc="lower left")
    plt.grid(alpha=0.3)
    plt.savefig(os.path.join(output_dir, f"model_{model_name}_pr_curve.png"),
                dpi=300, bbox_inches='tight')
    plt.close()

    # Save PR curve data
    pd.DataFrame({'recall': recall_curve, 'precision': precision_curve}).to_csv(
        os.path.join(output_dir, f"model_{model_name}_pr_curve.csv"),
        index=False
    )

    # Calculate metrics
    mcc = matthews_corrcoef(all_labels, binary_preds)
    accuracy = accuracy_score(all_labels, binary_preds)
    precision = precision_score(all_labels, binary_preds)
    recall = recall_score(all_labels, binary_preds)
    f1 = f1_score(all_labels, binary_preds)

    # Print summary
    tn, fp, fn, tp = conf_matrix.ravel()

    print(f"\n{'='*80}")
    print(f"EVALUATION SUMMARY FOR MODEL {model_name}")
    print(f"{'='*80}")
    print(f"MCC:        {mcc:.4f}")
    print(f"Accuracy:   {accuracy:.4f}")
    print(f"Precision:  {precision:.4f}")
    print(f"Recall:     {recall:.4f}")
    print(f"F1 Score:   {f1:.4f}")
    print(f"ROC AUC:    {roc_auc:.4f}")
    print(f"PR AUC:     {pr_auc:.4f}")

    print("\nConfusion Matrix:")
    print(f"  TN: {tn}, FP: {fp}")
    print(f"  FN: {fn}, TP: {tp}")

    n_pos = fn + tp
    n_neg = tn + fp
    print(f"Class balance: {n_pos} positive, {n_neg} negative ({n_pos/(n_pos+n_neg):.2%} positive)")
    print(f"{'='*80}\n")

    print(f"Plots saved to {output_dir}")

    # Save predictions and metrics
    predictions_df = pd.DataFrame({
        'strain': all_strains,
        'phage': all_phages,
        'true_label': all_labels,
        'prediction_prob': all_preds,
        'prediction_binary': binary_preds
    })

    predictions_df.to_csv(os.path.join(output_dir, f"model_{model_name}_predictions.csv"), index=False)

    metrics_df = pd.DataFrame({
        'metric': ['mcc', 'accuracy', 'precision', 'recall', 'f1', 'roc_auc', 'pr_auc'],
        'value': [mcc, accuracy, precision, recall, f1, roc_auc, pr_auc]
    })

    metrics_df.to_csv(os.path.join(output_dir, f"model_{model_name}_metrics.csv"), index=False)

    return {
        'mcc': mcc,
        'accuracy': accuracy,
        'precision': precision,
        'recall': recall,
        'f1': f1,
        'roc_auc': roc_auc,
        'pr_auc': pr_auc,
        'confusion_matrix': conf_matrix,
        'predictions_df': predictions_df
    }

results_dir = '/content/drive/MyDrive/Arkin/set_transformer_data/glm_optuna_pooling_cv'
interactions_path = '/content/drive/MyDrive/Arkin/phage_public_datasets/e_coli/interaction_matrix.csv'
strain_embeddings_path = '/content/drive/MyDrive/Arkin/set_transformer_data/embedding_experiments/ecoli/current_embeddings/strain'
phage_embeddings_path = '/content/drive/MyDrive/Arkin/set_transformer_data/embedding_experiments/ecoli/current_embeddings/phage'

# Process the best model
generate_plots_for_saved_model(
    results_dir=results_dir,
    model_name='best',
    interactions_path=interactions_path,
    strain_embeddings_path=strain_embeddings_path,
    phage_embeddings_path=phage_embeddings_path
)

Loading model from /content/drive/MyDrive/Arkin/set_transformer_data/glm_optuna_pooling_cv/models/final_model_best.pt
Error loading model: Weights only load failed. This file can still be loaded, to do so you have two options, do those steps only if you trust the source of the checkpoint. 
	(1) In PyTorch 2.6, we changed the default value of the `weights_only` argument in `torch.load` from `False` to `True`. Re-running `torch.load` with `weights_only` set to `False` will likely succeed, but it can result in arbitrary code execution. Do it only if you got the file from a trusted source.
	(2) Alternatively, to load with `weights_only=True` please check the recommended steps in the following error message.
	WeightsUnpickler error: Unsupported global: GLOBAL numpy._core.multiarray.scalar was not an allowed global by default. Please use `torch.serialization.add_safe_globals([scalar])` or the `torch.serialization.safe_globals([scalar])` context manager to allowlist this global if you trust t

{'mcc': np.float64(0.3441049541532808),
 'accuracy': 0.7884837962962963,
 'precision': 0.5310457516339869,
 'recall': 0.4226267880364109,
 'f1': 0.4706734250543085,
 'roc_auc': np.float64(0.7546492455365936),
 'pr_auc': np.float64(0.46181844856983756),
 'confusion_matrix': array([[2400,  287],
        [ 444,  325]]),
 'predictions_df':       strain     phage  true_label  prediction_prob  prediction_binary
 0     ECOR54  55989_P2           0         0.517637                  1
 1     ECOR52  55989_P2           0         0.517607                  1
 2     ECOR51  55989_P2           1         0.517616                  1
 3     NILS72  55989_P2           1         0.567400                  1
 4     NILS29  55989_P2           1         0.569938                  1
 ...      ...       ...         ...              ...                ...
 3451  ECOR17   LM40_P3           0         0.116181                  0
 3452  NILS04   LM40_P3           0         0.155521                  0
 3453  NILS05  

## Best Parameter Cross-Validation

In [ ]:
import os
import numpy as np
import pandas as pd
import torch
import torch.nn as nn
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime
from pathlib import Path
from tqdm import tqdm
from sklearn.model_selection import KFold
from sklearn.metrics import (
    accuracy_score, precision_score, recall_score, f1_score,
    matthews_corrcoef, roc_auc_score, average_precision_score, confusion_matrix,
    roc_curve, precision_recall_curve, auc
)
import json

def run_ten_fold_cv_with_best_params(
    optuna_results_dir,
    interactions_path,
    strain_embeddings_path,
    phage_embeddings_path,
    n_folds=10,
    random_state=42,
    output_dir=None
):
    """
    Run 10-fold cross-validation with best parameters from Optuna optimization.
    """
    # Set up timestamp and results directory
    timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")

    if output_dir is None:
        output_dir = f"ten_fold_cv_results_{timestamp}"

    # Create directory structure
    os.makedirs(output_dir, exist_ok=True)
    os.makedirs(os.path.join(output_dir, "fold_results"), exist_ok=True)
    os.makedirs(os.path.join(output_dir, "fold_plots"), exist_ok=True)
    os.makedirs(os.path.join(output_dir, "combined_results"), exist_ok=True)

    # Load best parameters from Optuna results
    best_params = load_best_params(optuna_results_dir)

    # Extract model and training parameters
    model_params = {
        'dropout': best_params.get('dropout', 0.1),
        'ln': best_params.get('ln', True),
        'classifier_hidden_layers': best_params.get('classifier_hidden_layers', 1),
        'classifier_hidden_dim': best_params.get('classifier_hidden_dim', None),
        'activation_function': best_params.get('activation_function', 'relu')
    }

    train_params = {
        'num_epochs': 75,  # Set a reasonable default
        'learning_rate': best_params.get('learning_rate', 5e-5),
        'batch_size': best_params.get('batch_size', 512),
        'patience': 10,  # Set a reasonable default
        'use_phage_weights': best_params.get('use_phage_weights', True),
        'scheduler_type': best_params.get('scheduler_type', 'one_cycle'),
        'warmup_ratio': best_params.get('warmup_ratio', 0.1),
        'weight_decay': best_params.get('weight_decay', 0.01)
    }

    # Get pooling type from best parameters
    pooling_type = best_params.get('pooling_type', 'mean')

    # Save configuration
    config = {
        'best_params': best_params,
        'model_params': model_params,
        'train_params': train_params,
        'interactions_path': interactions_path,
        'strain_embeddings_path': strain_embeddings_path,
        'phage_embeddings_path': phage_embeddings_path,
        'pooling_type': pooling_type,
        'n_folds': n_folds,
        'random_state': random_state,
        'timestamp': timestamp,
        'optuna_results_dir': optuna_results_dir
    }

    with open(os.path.join(output_dir, "config.json"), 'w') as f:
        json.dump(config, f, indent=4)

    # Get device
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    print(f"Using device: {device}")

    print(f"\n{'='*80}")
    print(f"STARTING {n_folds}-FOLD CROSS-VALIDATION WITH BEST PARAMETERS")
    print(f"{'='*80}")
    print(f"Optuna results directory: {optuna_results_dir}")
    print(f"Pooling type: {pooling_type}")
    print(f"Results directory: {output_dir}")
    print("\nBest parameters from Optuna:")
    for key, value in best_params.items():
        print(f"  {key}: {value}")
    print(f"{'='*80}")

    # Load data
    print("Loading embeddings...")
    strain_embeddings = load_embeddings_flexible(strain_embeddings_path)
    phage_embeddings = load_embeddings_flexible(phage_embeddings_path)

    print("Loading interaction data...")
    interactions_df = pd.read_csv(interactions_path)

    # Filter to ensure we have embeddings for all strains/phages
    strain_keys = set(strain_embeddings.keys())
    phage_keys = set(phage_embeddings.keys())

    filtered_df = interactions_df[
        interactions_df['strain'].isin(strain_keys) &
        interactions_df['phage'].isin(phage_keys)
    ]

    print(f"Original interactions: {len(interactions_df)}")
    print(f"Filtered interactions: {len(filtered_df)}")

    if len(filtered_df) == 0:
        raise ValueError("No interactions match the provided embeddings!")

    # Get unique strains for fold splitting
    unique_strains = filtered_df['strain'].unique()

    # Create KFold object for splitting by strain
    kf = KFold(n_splits=n_folds, shuffle=True, random_state=random_state)

    # Track metrics and predictions across folds
    fold_metrics = []
    all_predictions = []

    # Since we're having issues with precompute_pooled_embeddings,
    # let's implement it directly here to ensure it works as expected

    # Direct implementation of pooling
    print(f"Directly implementing {pooling_type} pooling...")
    pooled_strains = {}
    pooled_phages = {}

    # Apply pooling to each strain
    for strain_id, (embedding, _) in tqdm(strain_embeddings.items(), desc="Pooling strains"):
        # Convert to tensor
        embedding_tensor = torch.tensor(embedding, dtype=torch.float32)

        # Apply pooling
        if pooling_type == 'mean':
            pooled = torch.mean(embedding_tensor, dim=0)
        elif pooling_type == 'max':
            pooled = torch.max(embedding_tensor, dim=0)[0]
        elif pooling_type == 'median':
            pooled = torch.median(embedding_tensor, dim=0)[0]
        else:
            raise ValueError(f"Unknown pooling type: {pooling_type}")

        # Store pooled vector
        pooled_strains[strain_id] = pooled.numpy()

    # Apply pooling to each phage
    for phage_id, (embedding, _) in tqdm(phage_embeddings.items(), desc="Pooling phages"):
        # Convert to tensor
        embedding_tensor = torch.tensor(embedding, dtype=torch.float32)

        # Apply pooling
        if pooling_type == 'mean':
            pooled = torch.mean(embedding_tensor, dim=0)
        elif pooling_type == 'max':
            pooled = torch.max(embedding_tensor, dim=0)[0]
        elif pooling_type == 'median':
            pooled = torch.median(embedding_tensor, dim=0)[0]
        else:
            raise ValueError(f"Unknown pooling type: {pooling_type}")

        # Store pooled vector
        pooled_phages[phage_id] = pooled.numpy()

    print(f"Completed pooling for {len(pooled_strains)} strains and {len(pooled_phages)} phages")

    # Get embedding dimension
    first_strain_id = next(iter(pooled_strains))
    embedding_dim = pooled_strains[first_strain_id].shape[0]
    print(f"Embedding dimension: {embedding_dim}")

    # Run cross-validation
    for fold_idx, (train_idx, val_idx) in enumerate(kf.split(unique_strains)):
        fold_num = fold_idx + 1
        print(f"\n{'='*80}")
        print(f"FOLD {fold_num}/{n_folds}")
        print(f"{'='*80}")

        # Create fold-specific directories
        fold_dir = os.path.join(output_dir, "fold_results", f"fold_{fold_num}")
        os.makedirs(fold_dir, exist_ok=True)

        # Split strains into train and validation sets
        train_strains = unique_strains[train_idx]
        val_strains = unique_strains[val_idx]

        # Create dataframes based on strain splits
        train_df = filtered_df[filtered_df['strain'].isin(train_strains)]
        val_df = filtered_df[filtered_df['strain'].isin(val_strains)]

        print(f"Train set: {len(train_df)} interactions, {len(train_strains)} strains")
        print(f"Validation set: {len(val_df)} interactions, {len(val_strains)} strains")

        # Calculate phage-specific weights if needed
        phage_weights = {}
        if train_params.get('use_phage_weights', True):
            phage_weights = calculate_phage_specific_weights(train_df)
            print(f"Using phage-specific weights for {len(phage_weights)} phages")
        else:
            # Use a default weight of 1.0 for all phages
            for phage in train_df['phage'].unique():
                phage_weights[phage] = 1.0
            print("Using default weight of 1.0 for all phages")

        # Create datasets
        train_dataset = PrecomputedPooledDataset(train_df, pooled_strains, pooled_phages, phage_weights)
        val_dataset = PrecomputedPooledDataset(val_df, pooled_strains, pooled_phages, phage_weights)

        # Create dataloaders
        train_loader = torch.utils.data.DataLoader(
            train_dataset,
            batch_size=train_params.get('batch_size', 512),
            shuffle=True,
            collate_fn=collate_pooled_vectors
        )

        val_loader = torch.utils.data.DataLoader(
            val_dataset,
            batch_size=train_params.get('batch_size', 512),
            shuffle=False,
            collate_fn=collate_pooled_vectors
        )

        # Initialize model
        model = PooledVectorModel(
            embedding_dim=embedding_dim,
            dropout=model_params.get('dropout', 0.1),
            ln=model_params.get('ln', True),
            classifier_hidden_layers=model_params.get('classifier_hidden_layers', 1),
            classifier_hidden_dim=model_params.get('classifier_hidden_dim', None),
            activation_function=model_params.get('activation_function', 'relu')
        ).to(device)

        # Train the model
        history, val_score = train_model(
            model,
            train_loader,
            val_loader,
            None,  # No trial object
            num_epochs=train_params.get('num_epochs', 75),
            learning_rate=train_params.get('learning_rate', 5e-5),
            patience=train_params.get('patience', 10),
            device=device,
            use_phage_weights=train_params.get('use_phage_weights', True),
            scheduler_type=train_params.get('scheduler_type', 'one_cycle'),
            warmup_ratio=train_params.get('warmup_ratio', 0.1),
            weight_decay=train_params.get('weight_decay', 0.01),
            metrics_dir=os.path.join(output_dir, "fold_results")
        )

        # Save training history plot
        save_training_history_plot(history, fold_dir, fold_num)

        # Evaluate on validation set
        val_metrics = evaluate_full(model, val_loader, device, train_params.get('use_phage_weights', True))

        # Save model
        torch.save({
            'model_state_dict': model.state_dict(),
            'model_params': model_params,
            'train_params': train_params,
            'val_metrics': val_metrics,
            'fold': fold_num,
            'embedding_dim': embedding_dim
        }, os.path.join(fold_dir, f"model_fold_{fold_num}.pt"))

        # Save prediction results
        val_results = save_predictions(model, val_loader, device, fold_dir, train_params.get('use_phage_weights', True))

        # Add fold information
        val_results['fold'] = fold_num

        # Append to all predictions for combined analysis
        all_predictions.append(val_results)

        # Generate fold-specific plots
        generate_fold_plots(val_metrics, fold_num, output_dir)

        # Save detailed metrics
        fold_metrics.append({
            'fold': fold_num,
            'accuracy': val_metrics['accuracy'],
            'precision': val_metrics['precision'],
            'recall': val_metrics['recall'],
            'f1': val_metrics['f1'],
            'mcc': val_metrics['mcc'],
            'roc_auc': val_metrics['roc_auc'],
            'pr_auc': val_metrics['pr_auc'],
            'tn': val_metrics['conf_matrix'][0, 0],
            'fp': val_metrics['conf_matrix'][0, 1],
            'fn': val_metrics['conf_matrix'][1, 0],
            'tp': val_metrics['conf_matrix'][1, 1]
        })

        # Print fold results
        print(f"\nFold {fold_num} Results:")
        print(f"Accuracy: {val_metrics['accuracy']:.4f}")
        print(f"Precision: {val_metrics['precision']:.4f}")
        print(f"Recall: {val_metrics['recall']:.4f}")
        print(f"F1: {val_metrics['f1']:.4f}")
        print(f"MCC: {val_metrics['mcc']:.4f}")
        print(f"ROC AUC: {val_metrics['roc_auc']:.4f}")
        print(f"PR AUC: {val_metrics['pr_auc']:.4f}")

    # Create metrics DataFrame
    metrics_df = pd.DataFrame(fold_metrics)

    # Combine all predictions
    combined_preds_df = pd.concat(all_predictions, ignore_index=True)
    combined_preds_df.to_csv(os.path.join(output_dir, "combined_results", "all_predictions.csv"), index=False)

    # Generate combined plots and statistics
    combined_results = generate_combined_results(metrics_df, combined_preds_df, output_dir)

    # Save fold metrics
    metrics_df.to_csv(os.path.join(output_dir, "combined_results", "fold_metrics.csv"), index=False)

    # Print final summary
    print_final_summary(combined_results, output_dir)

    # Return all results
    return {
        'metrics_df': metrics_df,
        'combined_preds_df': combined_preds_df,
        'combined_results': combined_results,
        'output_dir': output_dir
    }

def load_best_params(optuna_results_dir):
    """
    Load the best parameters from Optuna optimization results.

    Args:
        optuna_results_dir: Directory containing Optuna results

    Returns:
        Dictionary with best parameters
    """
    # Try to find best_params.json or best_params_cv.json
    best_params_paths = [
        os.path.join(optuna_results_dir, "best_params.json"),
        os.path.join(optuna_results_dir, "best_params_cv.json")
    ]

    for path in best_params_paths:
        if os.path.exists(path):
            print(f"Loading best parameters from {path}")
            with open(path, 'r') as f:
                return json.load(f)

    # If not found, try to load from study.pkl
    study_path = os.path.join(optuna_results_dir, "study.pkl")
    if os.path.exists(study_path):
        import pickle
        print(f"Loading study from {study_path}")
        with open(study_path, 'rb') as f:
            study = pickle.load(f)
        return study.best_params

    raise ValueError(f"Could not find best parameters in {optuna_results_dir}")

def save_predictions(model, data_loader, device, output_dir, use_phage_weights=True):
    """
    Generate and save detailed prediction results.

    Args:
        model: Trained model
        data_loader: DataLoader with test/validation data
        device: Device to run evaluation on
        output_dir: Directory to save results
        use_phage_weights: Whether to use phage-specific weights

    Returns:
        DataFrame with predictions
    """
    model.eval()

    # Lists to store results
    strain_ids = []
    phage_ids = []
    true_labels = []
    predicted_probs = []
    predicted_labels = []

    with torch.no_grad():
        for batch in data_loader:
            # Unpack the batch (for pooled vectors: strain, phage, label, weight, strain_id, phage_id)
            strain_vec, phage_vec, labels, weights, s_ids, p_ids = batch

            strain_vec = strain_vec.to(device)
            phage_vec = phage_vec.to(device)
            labels = labels.to(device)

            logits = model(strain_vec, phage_vec)
            probs = torch.sigmoid(logits).cpu().numpy().flatten()
            preds = (probs > 0.5).astype(int)

            # Extend lists
            strain_ids.extend(s_ids)
            phage_ids.extend(p_ids)
            true_labels.extend(labels.cpu().numpy().flatten())
            predicted_probs.extend(probs)
            predicted_labels.extend(preds)

    # Create DataFrame
    results_df = pd.DataFrame({
        'strain': strain_ids,
        'phage': phage_ids,
        'true_label': true_labels,
        'confidence': predicted_probs,
        'predicted_label': predicted_labels
    })

    # Save to CSV
    results_df.to_csv(os.path.join(output_dir, "predictions.csv"), index=False)

    return results_df

def generate_fold_plots(metrics, fold_num, output_dir):
    """
    Generate and save fold-specific plots.

    Args:
        metrics: Dictionary with evaluation metrics
        fold_num: Fold number
        output_dir: Base output directory
    """
    plots_dir = os.path.join(output_dir, "fold_plots")
    os.makedirs(plots_dir, exist_ok=True)

    # Calculate ROC curve if not already in metrics
    if 'fpr' not in metrics or 'tpr' not in metrics:
        fpr, tpr, _ = roc_curve(metrics['all_labels'], metrics['all_preds'])
        roc_auc = metrics['roc_auc']  # Use the pre-calculated AUC
    else:
        fpr, tpr = metrics['fpr'], metrics['tpr']
        roc_auc = metrics['roc_auc']

    # 1. ROC Curve
    plt.figure(figsize=(8, 7))
    plt.plot(fpr, tpr, color='darkorange', lw=2,
             label=f'ROC curve (area = {roc_auc:.3f})')
    plt.plot([0, 1], [0, 1], color='navy', lw=2, linestyle='--')
    plt.xlim([0.0, 1.0])
    plt.ylim([0.0, 1.05])
    plt.xlabel('False Positive Rate')
    plt.ylabel('True Positive Rate')
    plt.title(f'ROC Curve - Fold {fold_num}')
    plt.legend(loc="lower right")
    plt.grid(alpha=0.3)
    plt.savefig(os.path.join(plots_dir, f"fold_{fold_num}_roc_curve.png"), dpi=300, bbox_inches='tight')
    plt.close()

    # Save ROC data
    roc_df = pd.DataFrame({'fpr': fpr, 'tpr': tpr, 'auc': roc_auc})
    roc_df.to_csv(os.path.join(output_dir, "fold_results", f"fold_{fold_num}", f"fold_{fold_num}_roc_curve.csv"),
                  index=False)

    # Calculate PR curve if not already in metrics
    if 'precision_curve' not in metrics or 'recall_curve' not in metrics:
        precision, recall, _ = precision_recall_curve(metrics['all_labels'], metrics['all_preds'])
        pr_auc = metrics['pr_auc']  # Use the pre-calculated AUC
    else:
        precision, recall = metrics['precision_curve'], metrics['recall_curve']
        pr_auc = metrics['pr_auc']

    # 2. Precision-Recall Curve
    plt.figure(figsize=(8, 7))
    plt.plot(recall, precision, color='darkorange', lw=2,
             label=f'PR curve (area = {pr_auc:.3f})')
    plt.xlim([0.0, 1.0])
    plt.ylim([0.0, 1.05])
    plt.xlabel('Recall')
    plt.ylabel('Precision')
    plt.title(f'Precision-Recall Curve - Fold {fold_num}')
    plt.legend(loc="lower left")
    plt.grid(alpha=0.3)
    plt.savefig(os.path.join(plots_dir, f"fold_{fold_num}_pr_curve.png"), dpi=300, bbox_inches='tight')
    plt.close()

    # Save PR data
    pr_df = pd.DataFrame({'recall': recall, 'precision': precision, 'auc': pr_auc})
    pr_df.to_csv(os.path.join(output_dir, "fold_results", f"fold_{fold_num}", f"fold_{fold_num}_pr_curve.csv"),
                 index=False)

    # 3. Confusion Matrix
    cm = metrics['conf_matrix']

    plt.figure(figsize=(8, 7))
    sns.heatmap(cm, annot=True, fmt="d", cmap="Blues", cbar=False,
                xticklabels=['Predicted Negative', 'Predicted Positive'],
                yticklabels=['Actual Negative', 'Actual Positive'])
    plt.title(f"Confusion Matrix - Fold {fold_num}")
    plt.xlabel("Predicted Label")
    plt.ylabel("True Label")
    plt.savefig(os.path.join(plots_dir, f"fold_{fold_num}_confusion_matrix.png"), dpi=300, bbox_inches='tight')
    plt.close()

    # Save confusion matrix data
    cm_df = pd.DataFrame(cm,
                         columns=['Predicted Negative', 'Predicted Positive'],
                         index=['Actual Negative', 'Actual Positive'])
    cm_df.to_csv(os.path.join(output_dir, "fold_results", f"fold_{fold_num}", f"fold_{fold_num}_confusion_matrix.csv"))

def generate_combined_results(metrics_df, predictions_df, output_dir):
    """
    Generate combined plots and metrics across all folds.

    Args:
        metrics_df: DataFrame with metrics for each fold
        predictions_df: DataFrame with all predictions
        output_dir: Base output directory

    Returns:
        Dictionary with combined metrics
    """
    combined_dir = os.path.join(output_dir, "combined_results")
    os.makedirs(combined_dir, exist_ok=True)

    # Extract all true labels and predictions
    y_true = predictions_df['true_label'].values
    y_pred_proba = predictions_df['confidence'].values
    y_pred = (y_pred_proba >= 0.5).astype(int)

    # Calculate combined confusion matrix
    cm = confusion_matrix(y_true, y_pred)
    tn, fp, fn, tp = cm.ravel()

    # Calculate combined metrics
    accuracy = accuracy_score(y_true, y_pred)
    precision = precision_score(y_true, y_pred)
    recall = recall_score(y_true, y_pred)
    f1 = f1_score(y_true, y_pred)
    mcc = matthews_corrcoef(y_true, y_pred)
    roc_auc = roc_auc_score(y_true, y_pred_proba)
    pr_auc = average_precision_score(y_true, y_pred_proba)

    # Calculate ROC and PR curves
    fpr, tpr, _ = roc_curve(y_true, y_pred_proba)
    precision_curve, recall_curve, _ = precision_recall_curve(y_true, y_pred_proba)

    # Calculate aggregate statistics across folds
    agg_metrics = {}
    for metric in ['accuracy', 'precision', 'recall', 'f1', 'mcc', 'roc_auc', 'pr_auc']:
        agg_metrics[metric] = {
            'mean': metrics_df[metric].mean(),
            'std': metrics_df[metric].std(),
            'median': metrics_df[metric].median(),
            'min': metrics_df[metric].min(),
            'max': metrics_df[metric].max()
        }

    # Create summary DataFrame
    summary_data = []
    for metric, values in agg_metrics.items():
        summary_data.append({
            'Metric': metric,
            'Mean': values['mean'],
            'Std': values['std'],
            'Median': values['median'],
            'Min': values['min'],
            'Max': values['max']
        })
    summary_df = pd.DataFrame(summary_data)
    summary_df.to_csv(os.path.join(combined_dir, "summary_metrics.csv"), index=False)

    # Save combined confusion matrix
    plt.figure(figsize=(10, 8))
    sns.heatmap(cm, annot=True, fmt="d", cmap="Blues", cbar=False,
                xticklabels=['Predicted Negative', 'Predicted Positive'],
                yticklabels=['Actual Negative', 'Actual Positive'])
    plt.title("Combined Confusion Matrix (All Folds)")
    plt.xlabel("Predicted Label")
    plt.ylabel("True Label")
    plt.savefig(os.path.join(combined_dir, "combined_confusion_matrix.png"), dpi=300, bbox_inches='tight')
    plt.close()

    # Save combined confusion matrix data
    cm_df = pd.DataFrame(cm,
                       columns=['Predicted Negative', 'Predicted Positive'],
                       index=['Actual Negative', 'Actual Positive'])
    cm_df.to_csv(os.path.join(combined_dir, "combined_confusion_matrix.csv"))

    # Save combined metrics
    combined_metrics_df = pd.DataFrame([{
        'metric': 'Combined Results',
        'accuracy': accuracy,
        'precision': precision,
        'recall': recall,
        'f1': f1,
        'mcc': mcc,
        'roc_auc': roc_auc,
        'pr_auc': pr_auc,
        'tp': tp,
        'fp': fp,
        'tn': tn,
        'fn': fn
    }])
    combined_metrics_df.to_csv(os.path.join(combined_dir, "combined_metrics.csv"), index=False)

    # Generate ROC curves for all folds on the same plot
    plt.figure(figsize=(12, 10))

    # Get ROC curves for individual folds
    for fold in sorted(predictions_df['fold'].unique()):
        fold_data = predictions_df[predictions_df['fold'] == fold]
        fold_fpr, fold_tpr, _ = roc_curve(fold_data['true_label'], fold_data['confidence'])
        fold_auc = auc(fold_fpr, fold_tpr)
        plt.plot(fold_fpr, fold_tpr, lw=1, alpha=0.6, label=f'Fold {fold} (AUC = {fold_auc:.3f})')

    # Add combined ROC curve
    plt.plot(fpr, tpr, color='blue', lw=2, alpha=0.9,
             label=f'Combined (AUC = {roc_auc:.3f})')

    plt.plot([0, 1], [0, 1], 'k--', lw=2)
    plt.xlim([0.0, 1.0])
    plt.ylim([0.0, 1.05])
    plt.xlabel('False Positive Rate')
    plt.ylabel('True Positive Rate')
    plt.title('ROC Curves for All Folds')
    plt.legend(loc="lower right")
    plt.grid(alpha=0.3)
    plt.savefig(os.path.join(combined_dir, "all_folds_roc_curve.png"), dpi=300, bbox_inches='tight')
    plt.close()

    # Save mean ROC data
    roc_df = pd.DataFrame({'fpr': fpr, 'tpr': tpr, 'auc': roc_auc})
    roc_df.to_csv(os.path.join(combined_dir, "combined_roc_curve.csv"), index=False)

    # Generate PR curves for all folds on the same plot
    plt.figure(figsize=(12, 10))

    # Get PR curves for individual folds
    for fold in sorted(predictions_df['fold'].unique()):
        fold_data = predictions_df[predictions_df['fold'] == fold]
        fold_precision, fold_recall, _ = precision_recall_curve(fold_data['true_label'], fold_data['confidence'])
        fold_auc = auc(fold_recall, fold_precision)
        plt.plot(fold_recall, fold_precision, lw=1, alpha=0.6, label=f'Fold {fold} (AUC = {fold_auc:.3f})')

    # Add combined PR curve
    plt.plot(recall_curve, precision_curve, color='blue', lw=2, alpha=0.9,
             label=f'Combined (AUC = {pr_auc:.3f})')

    plt.xlim([0.0, 1.0])
    plt.ylim([0.0, 1.05])
    plt.xlabel('Recall')
    plt.ylabel('Precision')
    plt.title('Precision-Recall Curves for All Folds')
    plt.legend(loc="lower left")
    plt.grid(alpha=0.3)
    plt.savefig(os.path.join(combined_dir, "all_folds_pr_curve.png"), dpi=300, bbox_inches='tight')
    plt.close()

    # Save PR data
    pr_df = pd.DataFrame({'recall': recall_curve, 'precision': precision_curve, 'auc': pr_auc})
    pr_df.to_csv(os.path.join(combined_dir, "combined_pr_curve.csv"), index=False)

    # Plot metrics across folds
    plt.figure(figsize=(15, 12))
    metrics_to_plot = ['accuracy', 'precision', 'recall', 'f1', 'mcc', 'roc_auc', 'pr_auc']

    for i, metric in enumerate(metrics_to_plot):
        plt.subplot(3, 3, i+1)
        sns.barplot(x='fold', y=metric, data=metrics_df, color='skyblue')
        plt.axhline(y=metrics_df[metric].mean(), color='red', linestyle='-',
                    label=f'Mean: {metrics_df[metric].mean():.3f}')
        plt.xlabel('Fold')
        plt.ylabel(metric.capitalize())
        plt.title(f'{metric.capitalize()} by Fold')
        plt.legend()
        plt.grid(alpha=0.3)

    plt.tight_layout()
    plt.savefig(os.path.join(combined_dir, "metrics_by_fold.png"), dpi=300, bbox_inches='tight')
    plt.close()

    # Return combined results
    return {
        'confusion_matrix': cm,
        'accuracy': accuracy,
        'precision': precision,
        'recall': recall,
        'f1': f1,
        'mcc': mcc,
        'roc_auc': roc_auc,
        'pr_auc': pr_auc,
        'tp': int(tp),
        'fp': int(fp),
        'tn': int(tn),
        'fn': int(fn),
        'fpr': fpr,
        'tpr': tpr,
        'precision_curve': precision_curve,
        'recall_curve': recall_curve,
        'agg_metrics': agg_metrics,
        'summary_df': summary_df
    }

def print_final_summary(combined_results, output_dir):
    """
    Print final summary of cross-validation results.

    Args:
        combined_results: Dictionary with combined metrics
        output_dir: Output directory
    """
    agg_metrics = combined_results['agg_metrics']

    print(f"\n{'='*80}")
    print(f"CROSS-VALIDATION RESULTS SUMMARY")
    print(f"{'='*80}")
    print(f"Mean Accuracy: {agg_metrics['accuracy']['mean']:.4f} ± {agg_metrics['accuracy']['std']:.4f}")
    print(f"Mean Precision: {agg_metrics['precision']['mean']:.4f} ± {agg_metrics['precision']['std']:.4f}")
    print(f"Mean Recall: {agg_metrics['recall']['mean']:.4f} ± {agg_metrics['recall']['std']:.4f}")
    print(f"Mean F1: {agg_metrics['f1']['mean']:.4f} ± {agg_metrics['f1']['std']:.4f}")
    print(f"Mean MCC: {agg_metrics['mcc']['mean']:.4f} ± {agg_metrics['mcc']['std']:.4f}")
    print(f"Mean ROC AUC: {agg_metrics['roc_auc']['mean']:.4f} ± {agg_metrics['roc_auc']['std']:.4f}")
    print(f"Mean PR AUC: {agg_metrics['pr_auc']['mean']:.4f} ± {agg_metrics['pr_auc']['std']:.4f}")

    print("\nCombined metrics (across all fold predictions):")
    print(f"Combined Accuracy: {combined_results['accuracy']:.4f}")
    print(f"Combined Precision: {combined_results['precision']:.4f}")
    print(f"Combined Recall: {combined_results['recall']:.4f}")
    print(f"Combined F1: {combined_results['f1']:.4f}")
    print(f"Combined MCC: {combined_results['mcc']:.4f}")
    print(f"Combined ROC AUC: {combined_results['roc_auc']:.4f}")
    print(f"Combined PR AUC: {combined_results['pr_auc']:.4f}")

    print("\nConfusion Matrix:")
    print(f"TN: {combined_results['tn']}, FP: {combined_results['fp']}")
    print(f"FN: {combined_results['fn']}, TP: {combined_results['tp']}")

    print(f"{'='*80}")
    print(f"All results saved to: {output_dir}")

def save_training_history_plot(history, output_dir, fold_num):
    """
    Save training history plots (loss and metrics over epochs).

    Args:
        history: Dictionary containing training history
        output_dir: Directory to save plots
        fold_num: Fold number for filename
    """
    plt.figure(figsize=(15, 6))

    # Loss plot
    plt.subplot(1, 2, 1)
    plt.plot(range(1, len(history['train_loss']) + 1), history['train_loss'], 'b-', label='Training Loss')
    plt.plot(range(1, len(history['val_loss']) + 1), history['val_loss'], 'r-', label='Validation Loss')
    plt.xlabel('Epoch')
    plt.ylabel('Loss')
    plt.title(f'Fold {fold_num}: Loss vs. Epochs')
    plt.legend()
    plt.grid(alpha=0.3)

    # MCC plot
    plt.subplot(1, 2, 2)
    plt.plot(range(1, len(history['train_mcc']) + 1), history['train_mcc'], 'b-', label='Training MCC')
    plt.plot(range(1, len(history['val_mcc']) + 1), history['val_mcc'], 'r-', label='Validation MCC')
    plt.xlabel('Epoch')
    plt.ylabel('MCC')
    plt.title(f'Fold {fold_num}: MCC vs. Epochs')
    plt.legend()
    plt.grid(alpha=0.3)

    # Save the figure
    plt.tight_layout()
    plt.savefig(os.path.join(output_dir, f"history_fold_{fold_num}.png"), dpi=300, bbox_inches='tight')
    plt.close()

    # Save history data as CSV
    history_df = pd.DataFrame({
        'epoch': range(1, len(history['train_loss']) + 1),
        'train_loss': history['train_loss'],
        'val_loss': history['val_loss'],
        'train_mcc': history['train_mcc'],
        'val_mcc': history['val_mcc'],
        'lr': history.get('lr', [None] * len(history['train_loss']))  # Include learning rate if available
    })

    history_df.to_csv(os.path.join(output_dir, f"history_fold_{fold_num}.csv"), index=False)

    # Also save learning rate plot if available
    if 'lr' in history and any(lr is not None for lr in history['lr']):
        plt.figure(figsize=(8, 5))
        plt.plot(range(1, len(history['lr']) + 1), history['lr'], 'g-')
        plt.xlabel('Epoch')
        plt.ylabel('Learning Rate')
        plt.title(f'Fold {fold_num}: Learning Rate Schedule')
        plt.grid(alpha=0.3)
        plt.savefig(os.path.join(output_dir, f"lr_schedule_fold_{fold_num}.png"), dpi=300, bbox_inches='tight')
        plt.close()

In [ ]:
def analyze_cv_results(cv_results_dir):
    """
    Analyze cross-validation results to generate additional insights.

    Args:
        cv_results_dir: Directory containing CV results

    Returns:
        Dictionary with additional analysis
    """
    print(f"Analyzing results in: {cv_results_dir}")

    # Create directory for additional analysis
    analysis_dir = os.path.join(cv_results_dir, "analysis")
    os.makedirs(analysis_dir, exist_ok=True)

    # Load combined predictions
    predictions_path = os.path.join(cv_results_dir, "combined_results", "all_predictions.csv")
    if not os.path.exists(predictions_path):
        raise ValueError(f"Predictions file not found: {predictions_path}")

    all_preds_df = pd.read_csv(predictions_path)
    print(f"Loaded {len(all_preds_df)} predictions across all folds")

    # Extract true labels and predictions
    y_true = all_preds_df['true_label'].values
    y_pred_proba = all_preds_df['confidence'].values

    # Find optimal threshold using different metrics
    thresholds = np.linspace(0.1, 0.9, 81)  # Check thresholds from 0.1 to 0.9 in steps of 0.01

    # Arrays to store metrics for each threshold
    accuracies = []
    precisions = []
    recalls = []
    f1_scores = []
    mccs = []

    print("Finding optimal thresholds for different metrics...")
    for threshold in thresholds:
        y_pred = (y_pred_proba >= threshold).astype(int)

        accuracies.append(accuracy_score(y_true, y_pred))
        precisions.append(precision_score(y_true, y_pred))
        recalls.append(recall_score(y_true, y_pred))
        f1_scores.append(f1_score(y_true, y_pred))
        mccs.append(matthews_corrcoef(y_true, y_pred))

    # Find optimal thresholds
    optimal_thresholds = {
        'accuracy': thresholds[np.argmax(accuracies)],
        'precision': thresholds[np.argmax(precisions)],
        'recall': thresholds[np.argmax(recalls)],
        'f1': thresholds[np.argmax(f1_scores)],
        'mcc': thresholds[np.argmax(mccs)]
    }

    optimal_values = {
        'accuracy': np.max(accuracies),
        'precision': np.max(precisions),
        'recall': np.max(recalls),
        'f1': np.max(f1_scores),
        'mcc': np.max(mccs)
    }

    # Save thresholds
    thresholds_df = pd.DataFrame({
        'threshold': thresholds,
        'accuracy': accuracies,
        'precision': precisions,
        'recall': recalls,
        'f1': f1_scores,
        'mcc': mccs
    })
    thresholds_df.to_csv(os.path.join(analysis_dir, "threshold_analysis.csv"), index=False)

    # Plot threshold vs metrics
    plt.figure(figsize=(12, 8))
    plt.plot(thresholds, accuracies, label='Accuracy')
    plt.plot(thresholds, precisions, label='Precision')
    plt.plot(thresholds, recalls, label='Recall')
    plt.plot(thresholds, f1_scores, label='F1')
    plt.plot(thresholds, mccs, label='MCC')

    # Mark optimal thresholds
    for metric, threshold in optimal_thresholds.items():
        plt.axvline(x=threshold, color='gray', linestyle='--', alpha=0.5)
        plt.text(threshold, 0.4, f"{metric}: {threshold:.2f}", rotation=90, alpha=0.7)

    plt.xlabel('Threshold')
    plt.ylabel('Metric Value')
    plt.title('Effect of Classification Threshold on Metrics')
    plt.legend()
    plt.grid(alpha=0.3)
    plt.savefig(os.path.join(analysis_dir, "threshold_metrics.png"), dpi=300, bbox_inches='tight')
    plt.close()

    # Apply the optimal MCC threshold and recalculate metrics
    optimal_threshold = optimal_thresholds['mcc']
    y_pred_optimal = (y_pred_proba >= optimal_threshold).astype(int)

    # Recalculate confusion matrix and metrics
    cm_optimal = confusion_matrix(y_true, y_pred_optimal)

    optimal_metrics = {
        'threshold': optimal_threshold,
        'accuracy': accuracy_score(y_true, y_pred_optimal),
        'precision': precision_score(y_true, y_pred_optimal),
        'recall': recall_score(y_true, y_pred_optimal),
        'f1': f1_score(y_true, y_pred_optimal),
        'mcc': matthews_corrcoef(y_true, y_pred_optimal),
        'tn': cm_optimal[0, 0],
        'fp': cm_optimal[0, 1],
        'fn': cm_optimal[1, 0],
        'tp': cm_optimal[1, 1]
    }

    # Save optimal metrics
    with open(os.path.join(analysis_dir, "optimal_threshold_metrics.json"), 'w') as f:
        json.dump(optimal_metrics, f, indent=4)

    # Generate confusion matrix with optimal threshold
    plt.figure(figsize=(10, 8))
    sns.heatmap(cm_optimal, annot=True, fmt="d", cmap="Blues", cbar=False,
                xticklabels=['Predicted Negative', 'Predicted Positive'],
                yticklabels=['Actual Negative', 'Actual Positive'])
    plt.title(f"Confusion Matrix with Optimal Threshold ({optimal_threshold:.2f})")
    plt.xlabel("Predicted Label")
    plt.ylabel("True Label")
    plt.savefig(os.path.join(analysis_dir, "optimal_threshold_confusion_matrix.png"), dpi=300, bbox_inches='tight')
    plt.close()

    # Analysis by strain and phage
    if 'strain' in all_preds_df.columns and 'phage' in all_preds_df.columns:
        print("Analyzing performance by strain and phage...")

        # Group by strain
        strain_metrics = all_preds_df.groupby('strain').apply(lambda x: {
            'count': len(x),
            'accuracy': accuracy_score(x['true_label'], (x['confidence'] >= 0.5).astype(int)),
            'mcc': matthews_corrcoef(x['true_label'], (x['confidence'] >= 0.5).astype(int))
                  if len(set(x['true_label'])) > 1 else 0
        }).reset_index()

        # Convert to proper DataFrame
        strain_metrics_df = pd.DataFrame([
            {
                'strain': row['strain'],
                'count': row[0]['count'],
                'accuracy': row[0]['accuracy'],
                'mcc': row[0]['mcc']
            }
            for _, row in strain_metrics.iterrows()
        ])

        # Save strain metrics
        strain_metrics_df.to_csv(os.path.join(analysis_dir, "strain_performance.csv"), index=False)

        # Group by phage
        phage_metrics = all_preds_df.groupby('phage').apply(lambda x: {
            'count': len(x),
            'accuracy': accuracy_score(x['true_label'], (x['confidence'] >= 0.5).astype(int)),
            'mcc': matthews_corrcoef(x['true_label'], (x['confidence'] >= 0.5).astype(int))
                  if len(set(x['true_label'])) > 1 else 0
        }).reset_index()

        # Convert to proper DataFrame
        phage_metrics_df = pd.DataFrame([
            {
                'phage': row['phage'],
                'count': row[0]['count'],
                'accuracy': row[0]['accuracy'],
                'mcc': row[0]['mcc']
            }
            for _, row in phage_metrics.iterrows()
        ])

        # Save phage metrics
        phage_metrics_df.to_csv(os.path.join(analysis_dir, "phage_performance.csv"), index=False)

        # Plot strain performance
        plt.figure(figsize=(12, 8))

        # Filter to strains with sufficient data
        top_strains = strain_metrics_df[strain_metrics_df['count'] >= 10].sort_values('mcc', ascending=False)
        if len(top_strains) > 20:
            top_strains = top_strains.head(20)  # Limit to top 20 for readability

        sns.barplot(x='strain', y='mcc', data=top_strains)
        plt.xticks(rotation=90)
        plt.xlabel('Strain')
        plt.ylabel('MCC')
        plt.title('Performance by Strain (MCC)')
        plt.tight_layout()
        plt.savefig(os.path.join(analysis_dir, "strain_performance.png"), dpi=300, bbox_inches='tight')
        plt.close()

        # Plot phage performance
        plt.figure(figsize=(12, 8))

        # Filter to phages with sufficient data
        top_phages = phage_metrics_df[phage_metrics_df['count'] >= 10].sort_values('mcc', ascending=False)
        if len(top_phages) > 20:
            top_phages = top_phages.head(20)  # Limit to top 20 for readability

        sns.barplot(x='phage', y='mcc', data=top_phages)
        plt.xticks(rotation=90)
        plt.xlabel('Phage')
        plt.ylabel('MCC')
        plt.title('Performance by Phage (MCC)')
        plt.tight_layout()
        plt.savefig(os.path.join(analysis_dir, "phage_performance.png"), dpi=300, bbox_inches='tight')
        plt.close()

    # Print summary of analysis
    print(f"\n{'='*80}")
    print("ANALYSIS SUMMARY")
    print(f"{'='*80}")
    print(f"Optimal thresholds:")
    for metric, threshold in optimal_thresholds.items():
        print(f"  {metric}: {threshold:.3f} (value: {optimal_values[metric]:.4f})")
    print(f"\nRecalculated metrics with optimal threshold ({optimal_threshold:.3f}):")
    print(f"  Accuracy:  {optimal_metrics['accuracy']:.4f}")
    print(f"  Precision: {optimal_metrics['precision']:.4f}")
    print(f"  Recall:    {optimal_metrics['recall']:.4f}")
    print(f"  F1 Score:  {optimal_metrics['f1']:.4f}")
    print(f"  MCC:       {optimal_metrics['mcc']:.4f}")
    print(f"{'='*80}")
    print(f"Analysis results saved to: {analysis_dir}")

    return {
        'optimal_thresholds': optimal_thresholds,
        'optimal_values': optimal_values,
        'optimal_metrics': optimal_metrics,
        'analysis_dir': analysis_dir
    }

In [ ]:
def main_cv_workflow(
    interactions_path,
    strain_embeddings_path,
    phage_embeddings_path,
    pooling_type='mean',
    n_folds=10,
    random_state=42,
    output_dir=None
):
    """
    Run the complete 10-fold cross-validation workflow.

    Args:
        interactions_path: Path to CSV with interaction data
        strain_embeddings_path: Path to directory containing strain embeddings
        phage_embeddings_path: Path to directory containing phage embeddings
        pooling_type: Type of pooling to use ('mean', 'max', or 'median')
        n_folds: Number of folds for cross-validation
        random_state: Random seed for reproducibility
        output_dir: Output directory for results

    Returns:
        Dictionary with results
    """
    # Set timestamp for results directory
    timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")

    if output_dir is None:
        output_dir = f"cv_results_{pooling_type}_{timestamp}"

    print(f"\n{'='*80}")
    print(f"STARTING {n_folds}-FOLD CROSS-VALIDATION WORKFLOW")
    print(f"{'='*80}")
    print(f"Interactions file: {interactions_path}")
    print(f"Strain embeddings: {strain_embeddings_path}")
    print(f"Phage embeddings: {phage_embeddings_path}")
    print(f"Pooling type: {pooling_type}")
    print(f"Output directory: {output_dir}")
    print(f"{'='*80}\n")

    # Model parameters
    model_params = {
        'dropout': 0.1,
        'ln': True,
        'classifier_hidden_layers': 1,
        'classifier_hidden_dim': None,  # Will be set to embedding_dim if None
        'activation_function': 'relu'
    }

    # Training parameters
    train_params = {
        'num_epochs': 75,
        'learning_rate': 5e-5,
        'batch_size': 512,
        'patience': 10,
        'use_phage_weights': True,
        'scheduler_type': 'one_cycle',
        'warmup_ratio': 0.1,
        'weight_decay': 0.01
    }

    # Run cross-validation
    cv_results = run_ten_fold_cv(
        model_params=model_params,
        train_params=train_params,
        interactions_path=interactions_path,
        strain_embeddings_path=strain_embeddings_path,
        phage_embeddings_path=phage_embeddings_path,
        pooling_type=pooling_type,
        n_folds=n_folds,
        random_state=random_state,
        output_dir=output_dir
    )

    # Run additional analysis
    analysis_results = analyze_cv_results(output_dir)

    # Return combined results
    return {
        'cv_results': cv_results,
        'analysis_results': analysis_results,
        'output_dir': output_dir
    }

In [ ]:
results = run_ten_fold_cv_with_best_params(
    optuna_results_dir='/content/drive/MyDrive/Arkin/set_transformer_data/glm_optuna_pooling_cv',
    interactions_path = '/content/drive/MyDrive/Arkin/phage_public_datasets/e_coli/interaction_matrix.csv',
    strain_embeddings_path = '/content/drive/MyDrive/Arkin/set_transformer_data/embedding_experiments/ecoli/current_embeddings/strain',
    phage_embeddings_path = '/content/drive/MyDrive/Arkin/set_transformer_data/embedding_experiments/ecoli/current_embeddings/phage',
    n_folds=10,
    output_dir="/content/drive/MyDrive/Arkin/set_transformer_data/glm_optuna_pooling_cv/ten_fold_cv_results"
)

Loading best parameters from /content/drive/MyDrive/Arkin/set_transformer_data/glm_optuna_pooling_cv/best_params_cv.json
Using device: cuda

STARTING 10-FOLD CROSS-VALIDATION WITH BEST PARAMETERS
Optuna results directory: /content/drive/MyDrive/Arkin/set_transformer_data/glm_optuna_pooling_cv
Pooling type: mean
Results directory: /content/drive/MyDrive/Arkin/set_transformer_data/glm_optuna_pooling_cv/ten_fold_cv_results

Best parameters from Optuna:
  pooling_type: mean
  classifier_hidden_layers: 3
  classifier_hidden_dim: 512
  dropout: 0.1399261039732264
  ln: True
  activation_function: relu
  learning_rate: 5.924978444690761e-05
  batch_size: 512
  use_phage_weights: False
  weight_decay: 0.033737044834691504
  scheduler_type: cosine_annealing
  warmup_ratio: 0.18417067616941543
Loading embeddings...
Successfully loaded 177 embeddings
Successfully loaded 97 embeddings
Loading interaction data...
Original interactions: 38592
Filtered interactions: 16992
Directly implementing mean p

Pooling phages: 100%|██████████| 97/97 [00:00<00:00, 24924.80it/s]

Completed pooling for 177 strains and 97 phages
Embedding dimension: 384

FOLD 1/10
Train set: 15264 interactions, 159 strains
Validation set: 1728 interactions, 18 strains
Using default weight of 1.0 for all phages


Epoch 1/75 - Train Loss: 0.5342, MCC: -0.0019 | Val Loss: 0.4655, MCC: 0.0000 | LR: 0.000059
Epoch 2/75 - Train Loss: 0.5022, MCC: 0.0710 | Val Loss: 0.4525, MCC: 0.0639 | LR: 0.000059
Epoch 3/75 - Train Loss: 0.4929, MCC: 0.1214 | Val Loss: 0.4386, MCC: 0.0639 | LR: 0.000059
Epoch 4/75 - Train Loss: 0.4902, MCC: 0.1314 | Val Loss: 0.4525, MCC: 0.2317 | LR: 0.000059
Epoch 5/75 - Train Loss: 0.4903, MCC: 0.1575 | Val Loss: 0.4380, MCC: 0.1395 | LR: 0.000059
Epoch 6/75 - Train Loss: 0.4878, MCC: 0.1618 | Val Loss: 0.4394, MCC: 0.2317 | LR: 0.000058
Epoch 7/75 - Train Loss: 0.4845, MCC: 0.1550 | Val Loss: 0.4282, MCC: 0.2553 | LR: 0.000058
Epoch 8/75 - Train Loss: 0.4817, MCC: 0.1811 | Val Loss: 0.4239, MCC: 0.3579 | LR: 0.000058
Epoch 9/75 - Train Loss: 0.4792, MCC: 0.1917 | Val Loss: 0.4217, MCC: 0.2772 | LR: 0.000057
Epoch 10/75 - Train Loss: 0.4773, MCC: 0.2069 | Val Loss: 0.4234, MCC: 0.2509 | LR: 0.000057
Epoch 11/75 - Train Loss: 0.4766, MCC: 0.2073 | Val Loss: 0.4262, MCC: 0.3579 

In [ ]:
def display_study_results(study):
    """
    Display the results of an Optuna study in a notebook-friendly format.
    """
    import pandas as pd
    from IPython.display import display, HTML

    # Get best trial
    best_trial = study.best_trial

    # Create summary dataframe
    summary = pd.DataFrame({
        'Metric': ['Best Value (MCC)', 'Number of Trials', 'Study Duration'],
        'Value': [
            f"{best_trial.value:.4f}",
            len(study.trials),
            f"{(best_trial.datetime_complete - study.trials[0].datetime_start).total_seconds() / 3600:.1f} hours"
        ]
    })

    print("Study Summary:")
    display(summary)

    # Display best parameters
    params_df = pd.DataFrame({
        'Parameter': list(best_trial.params.keys()),
        'Value': list(best_trial.params.values())
    })

    print("\nBest Parameters:")
    display(params_df)

    # Display interactive plots if plotly is available
    try:
        import plotly.io as pio
        pio.renderers.default = 'notebook'

        print("\nOptimization History:")
        fig = optuna.visualization.plot_optimization_history(study)
        fig.show()

        print("\nParameter Importances:")
        fig = optuna.visualization.plot_param_importances(study)
        fig.show()

        print("\nParameter Relationships:")
        fig = optuna.visualization.plot_parallel_coordinate(study)
        fig.show()
    except:
        print("\nInstall plotly to see interactive visualizations: pip install plotly")

    # Display top trials
    top_trials = sorted(study.trials, key=lambda t: t.value if t.value is not None else float('-inf'), reverse=True)[:5]
    top_trials_data = []

    for t in top_trials:
        trial_data = {'Trial': t.number, 'Value': t.value if t.value is not None else None}
        for k, v in t.params.items():
            trial_data[k] = v
        top_trials_data.append(trial_data)

    print("\nTop 5 Trials:")
    display(pd.DataFrame(top_trials_data))

def print_final_summary(combined_results, output_dir):
    """
    Print final summary of cross-validation results.

    Args:
        combined_results: Dictionary with combined metrics
        output_dir: Output directory
    """
    agg_metrics = combined_results['agg_metrics']

    print(f"\n{'='*80}")
    print(f"CROSS-VALIDATION RESULTS SUMMARY")
    print(f"{'='*80}")
    print(f"Mean Accuracy: {agg_metrics['accuracy']['mean']:.4f} ± {agg_metrics['accuracy']['std']:.4f}")
    print(f"Mean Precision: {agg_metrics['precision']['mean']:.4f} ± {agg_metrics['precision']['std']:.4f}")
    print(f"Mean Recall: {agg_metrics['recall']['mean']:.4f} ± {agg_metrics['recall']['std']:.4f}")
    print(f"Mean F1: {agg_metrics['f1']['mean']:.4f} ± {agg_metrics['f1']['std']:.4f}")
    print(f"Mean MCC: {agg_metrics['mcc']['mean']:.4f} ± {agg_metrics['mcc']['std']:.4f}")
    print(f"Mean ROC AUC: {agg_metrics['roc_auc']['mean']:.4f} ± {agg_metrics['roc_auc']['std']:.4f}")
    print(f"Mean PR AUC: {agg_metrics['pr_auc']['mean']:.4f} ± {agg_metrics['pr_auc']['std']:.4f}")

    print("\nCombined metrics (across all fold predictions):")
    print(f"Combined Accuracy: {combined_results['accuracy']:.4f}")
    print(f"Combined Precision: {combined_results['precision']:.4f}")
    print(f"Combined Recall: {combined_results['recall']:.4f}")
    print(f"Combined F1: {combined_results['f1']:.4f}")
    print(f"Combined MCC: {combined_results['mcc']:.4f}")
    print(f"Combined ROC AUC: {combined_results['roc_auc']:.4f}")
    print(f"Combined PR AUC: {combined_results['pr_auc']:.4f}")

    print("\nConfusion Matrix:")
    print(f"TN: {combined_results['tn']}, FP: {combined_results['fp']}")
    print(f"FN: {combined_results['fn']}, TP: {combined_results['tp']}")

    print(f"{'='*80}")
    print(f"All results saved to: {output_dir}")

def analyze_cv_results(cv_results_dir):
    """
    Analyze cross-validation results to generate additional insights.

    Args:
        cv_results_dir: Directory containing CV results

    Returns:
        Dictionary with additional analysis
    """
    print(f"Analyzing results in: {cv_results_dir}")

    # Create directory for additional analysis
    analysis_dir = os.path.join(cv_results_dir, "analysis")
    os.makedirs(analysis_dir, exist_ok=True)

    # Load combined predictions
    predictions_path = os.path.join(cv_results_dir, "combined_results", "all_predictions.csv")
    if not os.path.exists(predictions_path):
        raise ValueError(f"Predictions file not found: {predictions_path}")

    all_preds_df = pd.read_csv(predictions_path)
    print(f"Loaded {len(all_preds_df)} predictions across all folds")

    # Extract true labels and predictions
    y_true = all_preds_df['true_label'].values
    y_pred_proba = all_preds_df['confidence'].values

    # Find optimal threshold using different metrics
    thresholds = np.linspace(0.1, 0.9, 81)  # Check thresholds from 0.1 to 0.9 in steps of 0.01

    # Arrays to store metrics for each threshold
    accuracies = []
    precisions = []
    recalls = []
    f1_scores = []
    mccs = []

    print("Finding optimal thresholds for different metrics...")
    for threshold in thresholds:
        y_pred = (y_pred_proba >= threshold).astype(int)

        accuracies.append(accuracy_score(y_true, y_pred))
        precisions.append(precision_score(y_true, y_pred))
        recalls.append(recall_score(y_true, y_pred))
        f1_scores.append(f1_score(y_true, y_pred))
        mccs.append(matthews_corrcoef(y_true, y_pred))

    # Find optimal thresholds
    optimal_thresholds = {
        'accuracy': thresholds[np.argmax(accuracies)],
        'precision': thresholds[np.argmax(precisions)],
        'recall': thresholds[np.argmax(recalls)],
        'f1': thresholds[np.argmax(f1_scores)],
        'mcc': thresholds[np.argmax(mccs)]
    }

    optimal_values = {
        'accuracy': np.max(accuracies),
        'precision': np.max(precisions),
        'recall': np.max(recalls),
        'f1': np.max(f1_scores),
        'mcc': np.max(mccs)
    }

    # Save thresholds
    thresholds_df = pd.DataFrame({
        'threshold': thresholds,
        'accuracy': accuracies,
        'precision': precisions,
        'recall': recalls,
        'f1': f1_scores,
        'mcc': mccs
    })
    thresholds_df.to_csv(os.path.join(analysis_dir, "threshold_analysis.csv"), index=False)

    # Plot threshold vs metrics
    plt.figure(figsize=(12, 8))
    plt.plot(thresholds, accuracies, label='Accuracy')
    plt.plot(thresholds, precisions, label='Precision')
    plt.plot(thresholds, recalls, label='Recall')
    plt.plot(thresholds, f1_scores, label='F1')
    plt.plot(thresholds, mccs, label='MCC')

    # Mark optimal thresholds
    for metric, threshold in optimal_thresholds.items():
        plt.axvline(x=threshold, color='gray', linestyle='--', alpha=0.5)
        plt.text(threshold, 0.4, f"{metric}: {threshold:.2f}", rotation=90, alpha=0.7)

    plt.xlabel('Threshold')
    plt.ylabel('Metric Value')
    plt.title('Effect of Classification Threshold on Metrics')
    plt.legend()
    plt.grid(alpha=0.3)
    plt.savefig(os.path.join(analysis_dir, "threshold_metrics.png"), dpi=300, bbox_inches='tight')
    plt.close()

    # Apply the optimal MCC threshold and recalculate metrics
    optimal_threshold = optimal_thresholds['mcc']
    y_pred_optimal = (y_pred_proba >= optimal_threshold).astype(int)

    # Recalculate confusion matrix and metrics
    cm_optimal = confusion_matrix(y_true, y_pred_optimal)

    optimal_metrics = {
        'threshold': optimal_threshold,
        'accuracy': accuracy_score(y_true, y_pred_optimal),
        'precision': precision_score(y_true, y_pred_optimal),
        'recall': recall_score(y_true, y_pred_optimal),
        'f1': f1_score(y_true, y_pred_optimal),
        'mcc': matthews_corrcoef(y_true, y_pred_optimal),
        'tn': cm_optimal[0, 0],
        'fp': cm_optimal[0, 1],
        'fn': cm_optimal[1, 0],
        'tp': cm_optimal[1, 1]
    }

    # Save optimal metrics
    with open(os.path.join(analysis_dir, "optimal_threshold_metrics.json"), 'w') as f:
        json.dump(optimal_metrics, f, indent=4)

    # Generate confusion matrix with optimal threshold
    plt.figure(figsize=(10, 8))
    sns.heatmap(cm_optimal, annot=True, fmt="d", cmap="Blues", cbar=False,
                xticklabels=['Predicted Negative', 'Predicted Positive'],
                yticklabels=['Actual Negative', 'Actual Positive'])
    plt.title(f"Confusion Matrix with Optimal Threshold ({optimal_threshold:.2f})")
    plt.xlabel("Predicted Label")
    plt.ylabel("True Label")
    plt.savefig(os.path.join(analysis_dir, "optimal_threshold_confusion_matrix.png"), dpi=300, bbox_inches='tight')
    plt.close()

    # Analysis by strain and phage
    if 'strain' in all_preds_df.columns and 'phage' in all_preds_df.columns:
        print("Analyzing performance by strain and phage...")

        # Group by strain
        strain_metrics = all_preds_df.groupby('strain').apply(lambda x: {
            'count': len(x),
            'accuracy': accuracy_score(x['true_label'], (x['confidence'] >= 0.5).astype(int)),
            'mcc': matthews_corrcoef(x['true_label'], (x['confidence'] >= 0.5).astype(int))
                  if len(set(x['true_label'])) > 1 else 0
        }).reset_index()

        # Convert to proper DataFrame
        strain_metrics_df = pd.DataFrame([
            {
                'strain': row['strain'],
                'count': row[0]['count'],
                'accuracy': row[0]['accuracy'],
                'mcc': row[0]['mcc']
            }
            for _, row in strain_metrics.iterrows()
        ])

        # Save strain metrics
        strain_metrics_df.to_csv(os.path.join(analysis_dir, "strain_performance.csv"), index=False)

        # Group by phage
        phage_metrics = all_preds_df.groupby('phage').apply(lambda x: {
            'count': len(x),
            'accuracy': accuracy_score(x['true_label'], (x['confidence'] >= 0.5).astype(int)),
            'mcc': matthews_corrcoef(x['true_label'], (x['confidence'] >= 0.5).astype(int))
                  if len(set(x['true_label'])) > 1 else 0
        }).reset_index()

        # Convert to proper DataFrame
        phage_metrics_df = pd.DataFrame([
            {
                'phage': row['phage'],
                'count': row[0]['count'],
                'accuracy': row[0]['accuracy'],
                'mcc': row[0]['mcc']
            }
            for _, row in phage_metrics.iterrows()
        ])

        # Save phage metrics
        phage_metrics_df.to_csv(os.path.join(analysis_dir, "phage_performance.csv"), index=False)

        # Plot strain performance
        plt.figure(figsize=(12, 8))

        # Filter to strains with sufficient data
        top_strains = strain_metrics_df[strain_metrics_df['count'] >= 10].sort_values('mcc', ascending=False)
        if len(top_strains) > 20:
            top_strains = top_strains.head(20)  # Limit to top 20 for readability

        sns.barplot(x='strain', y='mcc', data=top_strains)
        plt.xticks(rotation=90)
        plt.xlabel('Strain')
        plt.ylabel('MCC')
        plt.title('Performance by Strain (MCC)')
        plt.tight_layout()
        plt.savefig(os.path.join(analysis_dir, "strain_performance.png"), dpi=300, bbox_inches='tight')
        plt.close()

        # Plot phage performance
        plt.figure(figsize=(12, 8))

        # Filter to phages with sufficient data
        top_phages = phage_metrics_df[phage_metrics_df['count'] >= 10].sort_values('mcc', ascending=False)
        if len(top_phages) > 20:
            top_phages = top_phages.head(20)  # Limit to top 20 for readability

        sns.barplot(x='phage', y='mcc', data=top_phages)
        plt.xticks(rotation=90)
        plt.xlabel('Phage')
        plt.ylabel('MCC')
        plt.title('Performance by Phage (MCC)')
        plt.tight_layout()
        plt.savefig(os.path.join(analysis_dir, "phage_performance.png"), dpi=300, bbox_inches='tight')
        plt.close()

    # Print summary of analysis
    print(f"\n{'='*80}")
    print("ANALYSIS SUMMARY")
    print(f"{'='*80}")
    print(f"Optimal thresholds:")
    for metric, threshold in optimal_thresholds.items():
        print(f"  {metric}: {threshold:.3f} (value: {optimal_values[metric]:.4f})")
    print(f"\nRecalculated metrics with optimal threshold ({optimal_threshold:.3f}):")
    print(f"  Accuracy:  {optimal_metrics['accuracy']:.4f}")
    print(f"  Precision: {optimal_metrics['precision']:.4f}")
    print(f"  Recall:    {optimal_metrics['recall']:.4f}")
    print(f"  F1 Score:  {optimal_metrics['f1']:.4f}")
    print(f"  MCC:       {optimal_metrics['mcc']:.4f}")
    print(f"{'='*80}")
    print(f"Analysis results saved to: {analysis_dir}")

    return {
        'optimal_thresholds': optimal_thresholds,
        'optimal_values': optimal_values,
        'optimal_metrics': optimal_metrics,
        'analysis_dir': analysis_dir
    }